**Criação de DATABASE caso não exista**

In [8]:
IF NOT EXISTS
    (SELECT * FROM sys.databases WHERE name='DW_09') CREATE DATABASE DW_09
GO

Commands completed successfully.

Total execution time: 00:00:00.161

**Criação de SCHEMAS para alocar tabelas**

In [9]:
USE DW_09
GO

--CREATE SCHEMA STAGING
IF NOT EXISTS (SELECT 1 FROM sys.schemas WHERE name='STAGING')
    EXEC('CREATE SCHEMA STAGING');
GO

-- CREATE SCHEMA SILVER
IF NOT EXISTS (SELECT 1 FROM sys.schemas WHERE name='SILVER')
    EXEC('CREATE SCHEMA SILVER');
GO

-- CREATE SCHEMA GOLD
IF NOT EXISTS (SELECT 1 FROM sys.schemas WHERE name='GOLD')
    EXEC('CREATE SCHEMA GOLD');
GO

-- CREATE SCHEMA LOGS
IF NOT EXISTS (SELECT 1 FROM sys.schemas WHERE name='LOGS')
    EXEC('CREATE SCHEMA LOGS');
GO

Commands completed successfully.

Commands completed successfully.

Commands completed successfully.

Commands completed successfully.

Commands completed successfully.

Total execution time: 00:00:00.806

**Criação de tabela de Log**

In [10]:
USE [DW_09]
GO

IF NOT EXISTS (SELECT * FROM sysobjects WHERE name='LOG_CHALLENGE' AND xtype='U')

CREATE TABLE [DW_09].[LOGS].[LOG_CHALLENGE]
    (
        ID INT IDENTITY(1,1) NOT NULL PRIMARY KEY,
        NUMERO_ERRO INT,
        SERVERIDADE_ERRO INT,
        ESTADO_ERRO  INT,
        PROC_ERRO NVARCHAR(255),
        LINHA_ERRO INT,
        MSG_ERRO NVARCHAR(255),
        SITUACAO NVARCHAR(10),
        PROCESSO NVARCHAR(30),
        DATA_INI DATETIME,
        DATA_FIM DATETIME  
    )

Commands completed successfully.

Commands completed successfully.

Total execution time: 00:00:00.324

**Truncando tabela Log**

In [11]:
USE DW_09
GO

TRUNCATE TABLE [DW_09].[LOGS].[LOG_CHALLENGE]
GO

Commands completed successfully.

Commands completed successfully.

Total execution time: 00:00:00.329

**Criação de Tabela Staging para receber os dados**

In [12]:
USE DW_09
GO

IF NOT EXISTS (SELECT * FROM sysobjects WHERE NAME='STG_CHALLENGE' AND xtype='U')

CREATE TABLE [DW_09].[STAGING].[STG_CHALLENGE](
    [ANO_MES] nvarchar(10),
    [COD_ORG_SUPERIOR] nvarchar(150),
    [NOME_ORG_SUPERIOR] nvarchar(150),
    [COD_ORG_SUBORDINADO] nvarchar(150),
    [NOME_ORG_SUBORDINADO] nvarchar(150),

    [COD_UNID_GESTORA] nvarchar(150),
    [NOME_UNID_GESTORA] nvarchar(150),
    [COD_GESTAO] nvarchar(150),
    [NOME_GESTAO] nvarchar(150),
    [COD_UNID_ORCAMENTARIA] nvarchar(150),

    [NOME_UNID_ORCAMENTARIA] nvarchar(150),
    [COD_FUNCAO] nvarchar(150),
    [NOME_FUNCAO] nvarchar(150),
    [COD_SUBFUNCAO] nvarchar(150),
    [NOME_SUBFUNCAO] nvarchar(150),

    [COD_PROG_ORCAMENTARIO] nvarchar(150),
    [NOME_PROG_ORCAMENTARIO] nvarchar(150),
    [COD_ACAO] nvarchar(150),
    [NOME_ACAO] nvarchar(250),
    [COD_PLAN_ORCAMENTARIO] nvarchar(150),

    [NOME_PLAN_ORCAMENTARIO] nvarchar(250),
    [COD_PROG_GOVERNO] nvarchar(150),
    [NOME_PROG_GOVERNO] nvarchar(250),
    [UF] nvarchar(50),
    [MUNICIPIO] nvarchar(150),

    [COD_SUBTITULO] nvarchar(150),
    [NOME_SUBTITULO] nvarchar(150),
    [COD_LOCALIZADOR] nvarchar(150),
    [NOME_LOCALIZADOR] nvarchar(150),
    [SGL_LOCALIZADOR] nvarchar(150),

    [DESCR_COMP_LOCALIZADOR] nvarchar(150),
    [COD_AUTOR_EMENDA] nvarchar(150),
    [NOME_AUTOR_EMENDA] nvarchar(150),
    [COD_CAT_ECONOMICA] nvarchar(150),
    [NOME_CAT_ECONOMICA] nvarchar(150),

    [COD_GRP_DESPESA] nvarchar(150),
    [NOME_GRP_DESPESA] nvarchar(150),
    [COD_ELEMENTO_DESPESA] nvarchar(150),
    [NOME_ELEMENTO_DESPESA] nvarchar(150),
    [COD_MODALIDADE_DESPESA] nvarchar(150),

    [NOME_MODALIDADE_DESPESA] nvarchar(150),
    [VALOR_EMPENHADO] nvarchar(150),
    [VALOR_LIQUIDADO] nvarchar(150),
    [VALOR_PAGO] nvarchar(150),
    [VALOR_RESTOS_INSCRITOS] nvarchar(150),

    [VALOR_RESTOS_CANCELADOS] nvarchar(150),
    [VALOR_RESTOS_PAGOS] nvarchar(150)
) ON [PRIMARY]
GO

Commands completed successfully.

Commands completed successfully.

Total execution time: 00:00:00.325

**Truncando a tabela staging**

In [13]:
USE DW_09
GO

TRUNCATE TABLE [DW_09].[STAGING].[STG_CHALLENGE]
GO

Commands completed successfully.

Commands completed successfully.

Total execution time: 00:00:00.331

**Carregando dados na Tabela STG\_CHALLENGE**

Tabela 202201\_Despesas.csv

In [14]:
USE DW_09
GO

BEGIN TRANSACTION;
    DECLARE @VDATA_INI DATETIME;
    SET @VDATA_INI= GETDATE();

BEGIN TRY

-- INICIA BULK INSERT
BULK INSERT [DW_09].[STAGING].[STG_CHALLENGE] FROM 'C:\DWE2023\desafio\fontes\202201_Despesas.csv'
    WITH (
        CODEPAGE='65001',
        DATAFILETYPE='char',
        FIELDTERMINATOR = ';',
        ROWTERMINATOR = '\n',
        FIRE_TRIGGERS,
        FIRSTROW=2,
        MAXERRORS=2,
        FORMAT='CSV'
    )
-- TERMINA BULK INSERT

-- GRAVA LOG
INSERT INTO [DW_09].[LOGS].[LOG_CHALLENGE]
                ([NUMERO_ERRO],
                [SERVERIDADE_ERRO],
                [ESTADO_ERRO],
                [PROC_ERRO],
                [LINHA_ERRO],
                [MSG_ERRO],
                [SITUACAO],
                [PROCESSO],
                [DATA_INI],
                [DATA_FIM])
            VALUES
                (ERROR_NUMBER(),
                ERROR_SEVERITY(),
                ERROR_STATE(),
                ERROR_PROCEDURE(),
                ERROR_LINE(),
                ERROR_MESSAGE(),
                'SUCESSO',
                'CARGA STAGING',
                @VDATA_INI,
                GETDATE()
                )

IF @@TRANCOUNT > 0
        COMMIT TRANSACTION;

END TRY

BEGIN CATCH
-- GRAVA LOG DE ERRO
    IF @@TRANCOUNT > 0
        ROLLBACK TRANSACTION;

INSERT INTO [DW_09].[LOGS].[LOG_CHALLENGE]
            ([NUMERO_ERRO],
            [SERVERIDADE_ERRO],
            [ESTADO_ERRO],
            [PROC_ERRO],
            [LINHA_ERRO],
            [MSG_ERRO],
            [SITUACAO],
            [PROCESSO],
            [DATA_INI],
            [DATA_FIM])
        VALUES
            (ERROR_NUMBER(),
            ERROR_SEVERITY(),
            ERROR_STATE(),
            ERROR_PROCEDURE(),
            ERROR_LINE(),
            ERROR_MESSAGE(),
            'ERRO',
            'CARGA STAGING',
            @VDATA_INI,
            GETDATE()
            )
END CATCH;

Commands completed successfully.

(37530 rows affected)

(1 row affected)

Total execution time: 00:00:04.821

Tabela 202202\_Despesas.csv

In [15]:
USE DW_09
GO

BEGIN TRANSACTION;
    DECLARE @VDATA_INI DATETIME;
    SET @VDATA_INI= GETDATE();

BEGIN TRY
-- INICIA BULK INSERT
BULK INSERT [DW_09].[STAGING].[STG_CHALLENGE] FROM 'C:\DWE2023\desafio\fontes\202202_Despesas.csv'
    WITH (
        CODEPAGE='65001',
        DATAFILETYPE='char',
        FIELDTERMINATOR = ';',
        ROWTERMINATOR = '\n',
        FIRE_TRIGGERS,
        FIRSTROW=2,
        MAXERRORS=0,
        FORMAT='CSV'
    )
-- GRAVA LOG
INSERT INTO [DW_09].[LOGS].[LOG_CHALLENGE]
                ([NUMERO_ERRO],
                [SERVERIDADE_ERRO],
                [ESTADO_ERRO],
                [PROC_ERRO],
                [LINHA_ERRO],
                [MSG_ERRO],
                [SITUACAO],
                [PROCESSO],
                [DATA_INI],
                [DATA_FIM])
            VALUES
                (ERROR_NUMBER(),
                ERROR_SEVERITY(),
                ERROR_STATE(),
                ERROR_PROCEDURE(),
                ERROR_LINE(),
                ERROR_MESSAGE(),
                'SUCESSO',
                'CARGA STAGING',
                @VDATA_INI,
                GETDATE()
                )

IF @@TRANCOUNT > 0
        COMMIT TRANSACTION;
-- TERMINA BULK INSERT
END TRY

BEGIN CATCH
-- GRAVA LOG DE ERRO
    IF @@TRANCOUNT > 0
        ROLLBACK TRANSACTION;

INSERT INTO [DW_09].[LOGS].[LOG_CHALLENGE]
            ([NUMERO_ERRO],
            [SERVERIDADE_ERRO],
            [ESTADO_ERRO],
            [PROC_ERRO],
            [LINHA_ERRO],
            [MSG_ERRO],
            [SITUACAO],
            [PROCESSO],
            [DATA_INI],
            [DATA_FIM])
        VALUES
            (ERROR_NUMBER(),
            ERROR_SEVERITY(),
            ERROR_STATE(),
            ERROR_PROCEDURE(),
            ERROR_LINE(),
            ERROR_MESSAGE(),
            'ERRO',
            'CARGA STAGING',
            @VDATA_INI,
            GETDATE()
            )
END CATCH;

Commands completed successfully.

(50987 rows affected)

(1 row affected)

Total execution time: 00:00:04.273

Tabela 202203\_Despesas.csv

In [16]:
USE DW_09
GO

BEGIN TRANSACTION;
    DECLARE @VDATA_INI DATETIME;
    SET @VDATA_INI= GETDATE();

BEGIN TRY
-- INICIA BULK INSERT
BULK INSERT [DW_09].[STAGING].[STG_CHALLENGE] FROM 'C:\DWE2023\desafio\fontes\202203_Despesas.csv'
    WITH (
        CODEPAGE='65001',
        DATAFILETYPE='char',
        FIELDTERMINATOR = ';',
        ROWTERMINATOR = '\n',
        FIRE_TRIGGERS,
        FIRSTROW=2,
        MAXERRORS=0,
        FORMAT='CSV'
    )
-- GRAVA LOG
INSERT INTO [DW_09].[LOGS].[LOG_CHALLENGE]
                ([NUMERO_ERRO],
                [SERVERIDADE_ERRO],
                [ESTADO_ERRO],
                [PROC_ERRO],
                [LINHA_ERRO],
                [MSG_ERRO],
                [SITUACAO],
                [PROCESSO],
                [DATA_INI],
                [DATA_FIM])
            VALUES
                (ERROR_NUMBER(),
                ERROR_SEVERITY(),
                ERROR_STATE(),
                ERROR_PROCEDURE(),
                ERROR_LINE(),
                ERROR_MESSAGE(),
                'SUCESSO',
                'CARGA STAGING',
                @VDATA_INI,
                GETDATE()
                )

IF @@TRANCOUNT > 0
        COMMIT TRANSACTION;
-- TERMINIA BULK INSERT
END TRY

BEGIN CATCH
-- GRAVA LOG DE ERRO
    IF @@TRANCOUNT > 0
        ROLLBACK TRANSACTION;

INSERT INTO [DW_09].[LOGS].[LOG_CHALLENGE]
            ([NUMERO_ERRO],
            [SERVERIDADE_ERRO],
            [ESTADO_ERRO],
            [PROC_ERRO],
            [LINHA_ERRO],
            [MSG_ERRO],
            [SITUACAO],
            [PROCESSO],
            [DATA_INI],
            [DATA_FIM])
        VALUES
            (ERROR_NUMBER(),
            ERROR_SEVERITY(),
            ERROR_STATE(),
            ERROR_PROCEDURE(),
            ERROR_LINE(),
            ERROR_MESSAGE(),
            'ERRO',
            'CARGA STAGING',
            @VDATA_INI,
            GETDATE()
            )
END CATCH;

Commands completed successfully.

(57749 rows affected)

(1 row affected)

Total execution time: 00:00:03.369

**Corrigindo o formato das datas e valores**

In [17]:
USE DW_09

BEGIN TRANSACTION;
    DECLARE @VDATA_INI DATETIME;
    SET @VDATA_INI= GETDATE();

BEGIN TRY
-- INICIA UPDATE
UPDATE [DW_09].[STAGING].[STG_CHALLENGE]
SET [ANO_MES] = CONCAT([ANO_MES], '/01'),
    [VALOR_EMPENHADO] = REPLACE([VALOR_EMPENHADO], ',', '.'),
    [VALOR_LIQUIDADO] = REPLACE([VALOR_LIQUIDADO], ',', '.'),
    [VALOR_PAGO] = REPLACE([VALOR_PAGO], ',', '.'),
    [VALOR_RESTOS_INSCRITOS] = REPLACE([VALOR_RESTOS_INSCRITOS], ',', '.'),
    [VALOR_RESTOS_CANCELADOS] = REPLACE([VALOR_RESTOS_CANCELADOS], ',', '.'),
    [VALOR_RESTOS_PAGOS] = REPLACE([VALOR_RESTOS_PAGOS], ',', '.')
    WHERE 
        [VALOR_EMPENHADO] LIKE '%,%' 
        OR [VALOR_LIQUIDADO] LIKE '%,%' 
        OR [VALOR_PAGO] LIKE '%,%' 
        OR [VALOR_RESTOS_INSCRITOS] LIKE '%,%' 
        OR [VALOR_RESTOS_CANCELADOS] LIKE '%,%' 
        OR [VALOR_RESTOS_PAGOS] LIKE '%,%'
-- GRAVA LOG
INSERT INTO [DW_09].[LOGS].[LOG_CHALLENGE]
                ([NUMERO_ERRO],
                [SERVERIDADE_ERRO],
                [ESTADO_ERRO],
                [PROC_ERRO],
                [LINHA_ERRO],
                [MSG_ERRO],
                [SITUACAO],
                [PROCESSO],
                [DATA_INI],
                [DATA_FIM])
            VALUES
                (ERROR_NUMBER(),
                ERROR_SEVERITY(),
                ERROR_STATE(),
                ERROR_PROCEDURE(),
                ERROR_LINE(),
                ERROR_MESSAGE(),
                'SUCESSO',
                'UPDATE VALUES',
                @VDATA_INI,
                GETDATE()
                )

IF @@TRANCOUNT > 0
        COMMIT TRANSACTION;
-- TERMINA UPDATE
END TRY

BEGIN CATCH
-- GRAVA LOG DE ERRO
    IF @@TRANCOUNT > 0
        ROLLBACK TRANSACTION;

INSERT INTO [DW_09].[LOGS].[LOG_CHALLENGE]
            ([NUMERO_ERRO],
            [SERVERIDADE_ERRO],
            [ESTADO_ERRO],
            [PROC_ERRO],
            [LINHA_ERRO],
            [MSG_ERRO],
            [SITUACAO],
            [PROCESSO],
            [DATA_INI],
            [DATA_FIM])
        VALUES
            (ERROR_NUMBER(),
            ERROR_SEVERITY(),
            ERROR_STATE(),
            ERROR_PROCEDURE(),
            ERROR_LINE(),
            ERROR_MESSAGE(),
            'ERRO',
            'UPDATE VALUE',
            @VDATA_INI,
            GETDATE()
            )
END CATCH;

SELECT TOP 15 * FROM [DW_09].[STAGING].[STG_CHALLENGE]

(146266 rows affected)

(1 row affected)

(15 rows affected)

Total execution time: 00:00:05.396

ANO_MES COD_ORG_SUPERIOR NOME_ORG_SUPERIOR COD_ORG_SUBORDINADO NOME_ORG_SUBORDINADO COD_UNID_GESTORA NOME_UNID_GESTORA COD_GESTAO NOME_GESTAO COD_UNID_ORCAMENTARIA NOME_UNID_ORCAMENTARIA COD_FUNCAO NOME_FUNCAO COD_SUBFUNCAO NOME_SUBFUNCAO COD_PROG_ORCAMENTARIO NOME_PROG_ORCAMENTARIO COD_ACAO NOME_ACAO COD_PLAN_ORCAMENTARIO NOME_PLAN_ORCAMENTARIO COD_PROG_GOVERNO NOME_PROG_GOVERNO UF MUNICIPIO COD_SUBTITULO NOME_SUBTITULO COD_LOCALIZADOR NOME_LOCALIZADOR SGL_LOCALIZADOR DESCR_COMP_LOCALIZADOR COD_AUTOR_EMENDA NOME_AUTOR_EMENDA COD_CAT_ECONOMICA NOME_CAT_ECONOMICA COD_GRP_DESPESA NOME_GRP_DESPESA COD_ELEMENTO_DESPESA NOME_ELEMENTO_DESPESA COD_MODALIDADE_DESPESA NOME_MODALIDADE_DESPESA VALOR_EMPENHADO VALOR_LIQUIDADO VALOR_PAGO VALOR_RESTOS_INSCRITOS VALOR_RESTOS_CANCELADOS VALOR_RESTOS_PAGOS 2022/01/01 52000 Ministério da Defesa 52121 Comando do Exército 160322 HOSPITAL CENTRAL DO EXERCITO 00001 TESOURO NACIONAL 52121 COMANDO DO EXERCITO 05 Defesa nacional 128 Formação de recursos humanos 6012 DEFESA NACIONAL 8965 CAPACITACAO PROFISSIONAL MILITAR DO EXERCITO BRASILEIRO 0000 CAPACITACAO PROFISSIONAL MILITAR DO EXERCITO BRASILEIRO - DESPESAS DIVERSAS 00 NAO ATRIBUIDO NULL NULL 89650001 CAPACITACAO PROFISSIONAL MILITAR DO E - NACIONAL 0001 NACIONAL NA Sem informação NULL SEM EMENDA 3 DESPESAS CORRENTES 3 Outras Despesas Correntes 36 Outros Serviços de Terceiros - Pessoa Física 90 Reserva de Contingência 0.0000 0.0000 0.0000 0.0000 0.0000 106065.6000 2022/01/01 25000 Ministério da Economia 25000 Ministério da Economia - Unidades com vínculo direto 170106 GERENCIA REG.DE ADM.DO ME-MATO GROSSO DO SUL 00001 TESOURO NACIONAL 20118 AGENCIA BRASILEIRA DE INTELIGENCIA - ABIN 04 Administração 183 Informação e inteligência 4002 SEGURANCA INSTITUCIONAL 2684 ACOES DE INTELIGENCIA 2000 DESPESAS ADMINISTRATIVAS 00 NAO ATRIBUIDO NULL NULL 26840001 ACOES DE INTELIGENCIA - NACIONAL 0001 NACIONAL NA Sem informação NULL SEM EMENDA 3 DESPESAS CORRENTES 3 Outras Despesas Correntes 47 Obrigações Tributárias e Contributivas 90 Reserva de Contingência 0.0000 0.0000 0.0000 0.0000 0.0000 59.9700 2022/01/01 26000 Ministério da Educação 26241 Universidade Federal do Paraná 153079 UNIVERSIDADE FEDERAL DO PARANA 15232 UNIVERSIDADE FEDERAL DO PARANA 26241 UNIVERSIDADE FEDERAL DO PARANA 12 Educação 364 Ensino superior 5013 EDUCACAO SUPERIOR - GRADUACAO, POS-GRADUACAO, ENSINO, PESQUISA E EXTENSAO 20RK FUNCIONAMENTO DE INSTITUICOES FEDERAIS DE ENSINO SUPERIOR 0000 FUNCIONAMENTO DE INSTITUICOES FEDERAIS DE ENSINO SUPERIOR - DESPESAS DIVERSAS 00 NAO ATRIBUIDO PR NULL 20RK0041 FUNCIONAMENTO DE INSTITUICOES FEDERAI - NO ESTADO DO PARANA 0041 NO ESTADO DO PARANÁ PR Sem informação NULL SEM EMENDA 3 DESPESAS CORRENTES 3 Outras Despesas Correntes 41 Contribuições 50 Transferências a Instituições Privadas sem Fins Lucrativos 5972.0000 5972.0000 5972.0000 0.0000 0.0000 0.0000 2022/01/01 26000 Ministério da Educação 26437 Instituto Federal de Roraima 158152 INST.FED.DE EDUC.,CIENC.E TEC.DE RORAIMA 26437 INST.FED.DE EDUC.,CIENC.E TEC.DE RORAIMA 26437 INST.FED.DE EDUC.,CIENC.E TEC.DE RORAIMA 12 Educação 363 Ensino profissional 5012 EDUCACAO PROFISSIONAL E TECNOLOGICA 20RL FUNCIONAMENTO DAS INSTITUICOES DA REDE FEDERAL DE EDUCACAO PROFISSIONAL, CIENTIFICA E TECNOLOGICA 0000 FUNCIONAMENTO DAS INSTITUICOES DA REDE FEDERAL DE EDUCACAO PROFISSIONAL, CIENTIFICA E TECNOLOGICA 00 NAO ATRIBUIDO RR NULL 20RL0014 FUNCIONAMENTO DAS INSTITUICOES DA RED - NO ESTADO DE RORAIMA 0014 NO ESTADO DE RORAIMA RR Sem informação NULL SEM EMENDA 3 DESPESAS CORRENTES 3 Outras Despesas Correntes 47 Obrigações Tributárias e Contributivas 91 APLICACOES DIRETAS - OPER.INTRA-ORCAMENTARIAS 0.0000 0.0000 0.0000 0.0000 0.0000 157.6000 2022/01/01 26000 Ministério da Educação 26450 Universidade Federal do Sul da Bahia 158720 UNIVERSIDADE FEDERAL DO SUL DA BAHIA 26450 UNIVERSIDADE FEDERAL DO SUL DA BAHIA 26450 UNIVERSIDADE FEDERAL DO SUL DA BAHIA 12 Educação 364 Ensino superior 0032 PROGRAMA DE GESTAO E MANUTENCAO

**DIMENSÕES IDENTIFICADAS**  

- **D\_Org\_Superior | Tabela dimensão do Órgão Superior ||** 
    
    - SK\_ORG\_SUPERIOR | código SK do Órgão Superior || INT, NOT NULL, AUTO INCREMENT
    - ID\_COD | Código de ID do Órgão Superior || INT, NOT NULL UNIQUE
    - NOME\_ORG\_SUPERIOR | Nome do Órgão Superior || NVARCHAR (150), NOT NULL
    - DATA\_INI | Data de criação do item || DATATIME, NOT NULL
    - DATA\_FIM | Data de desativação do item || DATATIME
    - ATIVO | Booleano para o status de ativação do item || BIT
- **D\_Org\_Subordinado | Tabela dimensão do Órgão Superior ||** 
    
    - SK\_ORG\_SUBORDINADO | código SK do Órgão Subordinado|| INT, NOT NULL, AUTO INCREMENT
    - ID\_COD | Código de ID do Órgão Subordinado|| INT, NOT NULL UNIQUE
    - NOME\_ORG\_SUBORDINADO | Nome do Órgão Subordinado|| NVARCHAR (150), NOT NULL
    - DATA\_INI | Data de criação do item || DATATIME, NOT NULL
    - DATA\_FIM  | Data de desativação do item || DATATIME
    - ATIVO | Booleano para o status de ativação do item || BIT
- **D\_Unid\_Gestora | Tabela dimensão da Unidade Gestora ||** 
    
    - SK\_UNID\_GESTORA | código SK da Unidade Gestora || INT, NOT NULL, AUTO INCREMENT
    - ID\_COD | Código de ID da Unidade Gestora || INT, NOT NULL UNIQUE
    - NOME\_UNID\_GESTORA | Nome da Unidade Gestora || NVARCHAR (150), NOT NULL
    - DATA\_INI | Data de criação do item || DATATIME, NOT NULL
    - DATA\_FIM | Data de desativação do item || DATATIME
    - ATIVO | Booleano para o status de ativação do item || BIT
- **D\_Gestao | Tabela dimensão da Gestão ||** 
    
    - SK\_GESTAO | código SK da Gestão || INT, NOT NULL, AUTO INCREMENT
    - ID\_COD | Código de ID da Gestão || INT, NOT NULL UNIQUE
    - NOME\_GESTAO | Nome da Gestão || NVARCHAR (150), NOT NULL
    - DATA\_INI | Data de criação do item || DATATIME, NOT NULL
    - DATA\_FIM | Data de desativação do item || DATATIME
    - ATIVO | Booleano para o status de ativação do item || BIT
- **D\_Grp\_Despesa | Tabela dimensão do Grupo de Despesa ||** 
    
    - SK\_GRP\_DESPESA | código SK do Grupo de Despesa || INT, NOT NULL, AUTO INCREMENT
    - ID\_COD | Código de ID do Grupo de Despesa || INT, NOT NULL UNIQUE
    - NOME\_GRP\_DESPESA | Nome do Grupo de Despesa || NVARCHAR (150), NOT NULL
    - DATA\_INI | Data de criação do item || DATATIME, NOT NULL
    - DATA\_FIM | Data de desativação do item || DATATIME
    - ATIVO | Booleano para o status de ativação do item || BIT

**FATO IDENTIFICADAS**

- **F\_Despesa | Tabela fato conforme o pedido para análise das despesas ||** 
    - SK\_TRANSACAO | código SK da transação || INT, NOT NULL, AUTO INCREMENT
    - DATA\_MES | Data da Despesa || DATATIME, NOT NULL, 
    - SK\_ORG\_SUPERIOR | código SK do Órgão Superior || INT, NOT NULL, UNIQUE, 
    - SK\_ORG\_SUBORDINADO | código SK do Órgão Subordinado || INT, NOT NULL, UNIQUE, 
    - SK\_UNID\_GESTORA | código SK da Unidade Gestora || INT, NOT NULL, UNIQUE, 
    - SK\_GESTAO | código SK da Gestão || INT, NOT NULL, UNIQUE, 
    - SK\_GRP\_DESPESA | código SK do Grupo de Despesa || INT, NOT NULL, UNIQUE, 
    - VALOR\_EMPENHADO | Valor Empenhado || DECIMAL(15,2), NOT NULL, 
    - VALOR\_LIQUIDADO | Valor Liquidado || DECIMAL(15,2), NOT NULL, 
    - VALOR\_PAGO | Valor Pago || DECIMAL(15,2), NOT NULL

In [18]:
USE DW_09
GO

IF NOT EXISTS (SELECT * FROM sysobjects WHERE name='D_Org_Superior' AND xtype='U')
-- CRIAÇÃO DA TABELA DIMENSÃO DO ORGÃO SUPERIOR
CREATE TABLE [DW_09].[SILVER].[D_Org_Superior](
    [SK_ORG_SUPERIOR] INT IDENTITY(1,1) NOT NULL,
    [ID_COD] [INT] NOT NULL UNIQUE,
    [NOME_ORG_SUPERIOR] NVARCHAR(150) NOT NULL,
    [DATA_INI] DATETIME NOT NULL,
    [DATA_FIM] DATETIME,
    [ATIVO] BIT
    PRIMARY KEY CLUSTERED(
        [SK_ORG_SUPERIOR] ASC
    ) WITH (PAD_INDEX = OFF, STATISTICS_NORECOMPUTE = OFF, IGNORE_DUP_KEY = OFF, ALLOW_ROW_LOCKS = ON, ALLOW_PAGE_LOCKS = ON, OPTIMIZE_FOR_SEQUENTIAL_KEY = OFF) ON [PRIMARY]
) ON [PRIMARY]
GO

IF NOT EXISTS (SELECT * FROM sysobjects WHERE name='D_Org_Subordinado' AND xtype='U')
-- CRIAÇÃO DA TABELA DIMENSÃO DO ORGÃO SUBORDINADO
CREATE TABLE [DW_09].[SILVER].[D_Org_Subordinado](
    [SK_ORG_SUBORDINADO] INT IDENTITY(1,1) NOT NULL,
    [ID_COD] [INT] NOT NULL UNIQUE,
    [NOME_ORG_SUBORDINADO] NVARCHAR(150) NOT NULL,
    [DATA_INI] DATETIME,
    [DATA_FIM] DATETIME,
    [ATIVO] BIT
    PRIMARY KEY CLUSTERED( [SK_ORG_SUBORDINADO] ASC)
        WITH (PAD_INDEX = OFF, STATISTICS_NORECOMPUTE = OFF, IGNORE_DUP_KEY = OFF, ALLOW_ROW_LOCKS = ON, ALLOW_PAGE_LOCKS = ON, OPTIMIZE_FOR_SEQUENTIAL_KEY = OFF) ON [PRIMARY]
) ON [PRIMARY]
GO

IF NOT EXISTS (SELECT * FROM sysobjects WHERE name='D_Unid_Gestora' AND xtype='U')

-- CRIAÇÃO DA TABELA DIMENSÃO DA UNIDADE GESTORA
CREATE TABLE [DW_09].[SILVER].[D_Unid_Gestora](
    [SK_UNID_GESTORA] INT IDENTITY(1,1) NOT NULL,
    [ID_COD] [INT] NOT NULL UNIQUE,
    [NOME_UNID_GESTORA] NVARCHAR(250) NOT NULL,
    [DATA_INI] DATETIME,
    [DATA_FIM] DATETIME,
    [ATIVO] BIT
    PRIMARY KEY CLUSTERED( [SK_UNID_GESTORA] ASC)
        WITH (PAD_INDEX = OFF, STATISTICS_NORECOMPUTE = OFF, IGNORE_DUP_KEY = OFF, ALLOW_ROW_LOCKS = ON, ALLOW_PAGE_LOCKS = ON, OPTIMIZE_FOR_SEQUENTIAL_KEY = OFF) ON [PRIMARY]
) ON [PRIMARY]
GO

IF NOT EXISTS (SELECT * FROM sysobjects WHERE name='D_Gestao' AND xtype='U')

-- CRIAÇÃO DA TABELA DIMENSÃO DA GESTAO
CREATE TABLE [DW_09].[SILVER].[D_Gestao](
    [SK_GESTAO] INT IDENTITY(1,1) NOT NULL,
    [ID_COD] [INT] NOT NULL UNIQUE,
    [NOME_GESTAO] NVARCHAR(150) NOT NULL,
    [DATA_INI] DATETIME,
    [DATA_FIM] DATETIME,
    [ATIVO] BIT
    PRIMARY KEY CLUSTERED( [SK_GESTAO] ASC)
        WITH (PAD_INDEX = OFF, STATISTICS_NORECOMPUTE = OFF, IGNORE_DUP_KEY = OFF, ALLOW_ROW_LOCKS = ON, ALLOW_PAGE_LOCKS = ON, OPTIMIZE_FOR_SEQUENTIAL_KEY = OFF) ON [PRIMARY]
) ON [PRIMARY]
GO

IF NOT EXISTS (SELECT * FROM sysobjects WHERE name='D_Grp_Despesa' AND xtype='U')

-- CRIAÇÃO DA TABELA DIMENSÃO DO GRUPO DE DESPESA
CREATE TABLE [DW_09].[SILVER].[D_Grp_Despesa](
    [SK_GRP_DESPESA] INT IDENTITY(1,1) NOT NULL,
    [ID_COD] [INT] NOT NULL UNIQUE,
    [NOME_GRP_DESPESA] NVARCHAR(150) NOT NULL,
    [DATA_INI] DATETIME,
    [DATA_FIM] DATETIME,
    [ATIVO] BIT
    PRIMARY KEY CLUSTERED( [SK_GRP_DESPESA] ASC)
        WITH (PAD_INDEX = OFF, STATISTICS_NORECOMPUTE = OFF, IGNORE_DUP_KEY = OFF, ALLOW_ROW_LOCKS = ON, ALLOW_PAGE_LOCKS = ON, OPTIMIZE_FOR_SEQUENTIAL_KEY = OFF) ON [PRIMARY]
) ON [PRIMARY]
GO

Commands completed successfully.

Commands completed successfully.

Commands completed successfully.

Commands completed successfully.

Commands completed successfully.

Commands completed successfully.

Total execution time: 00:00:00.979

**Trucando as tabelas Dimensões**

In [19]:
USE DW_09
GO

TRUNCATE TABLE [DW_09].[SILVER].[D_Org_Superior]
GO
TRUNCATE TABLE [DW_09].[SILVER].[D_Org_Subordinado]
GO
TRUNCATE TABLE [DW_09].[SILVER].[D_Unid_Gestora]
GO
TRUNCATE TABLE [DW_09].[SILVER].[D_Gestao]
GO
TRUNCATE TABLE [DW_09].[SILVER].[D_Grp_Despesa]
GO

Commands completed successfully.

Commands completed successfully.

Commands completed successfully.

Commands completed successfully.

Commands completed successfully.

Commands completed successfully.

Total execution time: 00:00:01.055

**Carga Dimensao** D\_Org\_Superior

In [20]:
USE DW_09
GO

BEGIN TRANSACTION;
    DECLARE @VDATA_INI DATETIME;
    SET @VDATA_INI= GETDATE();

BEGIN TRY
-- INICIA MERGE
INSERT INTO [DW_09].[SILVER].[D_Org_Superior](ID_COD, NOME_ORG_SUPERIOR, DATA_INI, DATA_FIM, ATIVO)
SELECT ID_COD, NOME_ORG_SUPERIOR, DATA_INI, DATA_FIM, ATIVO
FROM (
    MERGE [DW_09].[SILVER].[D_Org_Superior] AS DESTINO 
    
    USING (
        SELECT DISTINCT COD_ORG_SUPERIOR, NOME_ORG_SUPERIOR
        FROM [DW_09].[STAGING].[STG_CHALLENGE] 
        WHERE COD_ORG_SUPERIOR IS NOT NULL 
            AND NOME_ORG_SUPERIOR IS NOT NULL
    ) AS ORIGEM
    
    ON DESTINO.[ID_COD] = ORIGEM.[COD_ORG_SUPERIOR]
        WHEN MATCHED 
            AND (DESTINO.NOME_ORG_SUPERIOR <> ORIGEM.NOME_ORG_SUPERIOR)
            AND DESTINO.ATIVO=1
        THEN
            UPDATE SET DESTINO.DATA_FIM = GETDATE(), DESTINO.ATIVO=0

        WHEN NOT MATCHED
        THEN
            INSERT (ID_COD, NOME_ORG_SUPERIOR, DATA_INI, DATA_FIM, ATIVO) VALUES (ORIGEM.COD_ORG_SUPERIOR, ORIGEM.NOME_ORG_SUPERIOR, GETDATE(), NULL, 1)
        OUTPUT $action,
            ORIGEM.COD_ORG_SUPERIOR,
            ORIGEM.NOME_ORG_SUPERIOR,
            GETDATE(),
            NULL,
            1
)
as changes
(
    action,
    ID_COD,
    NOME_ORG_SUPERIOR,
    DATA_INI,
    DATA_FIM,
    ATIVO
)
WHERE ACTION='UPDATE';
-- FIM MERGE

-- GRAVA LOG
INSERT INTO [DW_09].[LOGS].[LOG_CHALLENGE]
                ([NUMERO_ERRO],
                [SERVERIDADE_ERRO],
                [ESTADO_ERRO],
                [PROC_ERRO],
                [LINHA_ERRO],
                [MSG_ERRO],
                [SITUACAO],
                [PROCESSO],
                [DATA_INI],
                [DATA_FIM])
            VALUES
                (ERROR_NUMBER(),
                ERROR_SEVERITY(),
                ERROR_STATE(),
                ERROR_PROCEDURE(),
                ERROR_LINE(),
                ERROR_MESSAGE(),
                'SUCESSO',
                'CARGA DIMENSAO ORG SUPERIOR',
                @VDATA_INI,
                GETDATE()
                )

IF @@TRANCOUNT > 0
        SELECT @@TRANCOUNT, 'Sucesso';
        COMMIT TRANSACTION;

END TRY

BEGIN CATCH
-- GRAVA LOG DE ERRO
    SELECT @@TRANCOUNT, 'ERRO';
    IF @@TRANCOUNT > 0
        ROLLBACK TRANSACTION;

INSERT INTO [DW_09].[LOGS].[LOG_CHALLENGE]
            ([NUMERO_ERRO],
            [SERVERIDADE_ERRO],
            [ESTADO_ERRO],
            [PROC_ERRO],
            [LINHA_ERRO],
            [MSG_ERRO],
            [SITUACAO],
            [PROCESSO],
            [DATA_INI],
            [DATA_FIM])
        VALUES
            (ERROR_NUMBER(),
            ERROR_SEVERITY(),
            ERROR_STATE(),
            ERROR_PROCEDURE(),
            ERROR_LINE(),
            ERROR_MESSAGE(),
            'ERRO',
            'CARGA DIMENSOES ORG SUPERIOR',
            @VDATA_INI,
            GETDATE()
            )
END CATCH;

Commands completed successfully.

(0 rows affected)

(1 row affected)

(1 row affected)

Total execution time: 00:00:01.224

(No column name) (No column name) 1 Sucesso

**Carga Dimensao** D\_Org\_Subordinado

In [21]:
USE DW_09
GO

BEGIN TRANSACTION;
    DECLARE @VDATA_INI DATETIME;
    SET @VDATA_INI= GETDATE();

BEGIN TRY

-- INICIA MERGE
INSERT INTO [DW_09].[SILVER].[D_Org_Subordinado](ID_COD, NOME_ORG_SUBORDINADO, DATA_INI, DATA_FIM, ATIVO)
SELECT ID_COD, NOME_ORG_SUBORDINADO, DATA_INI, DATA_FIM, ATIVO
FROM (
    MERGE [DW_09].[SILVER].[D_Org_Subordinado] AS DESTINO 
    
    USING (
        SELECT DISTINCT COD_ORG_SUBORDINADO, NOME_ORG_SUBORDINADO 
        FROM [DW_09].[STAGING].[STG_CHALLENGE] 
        WHERE COD_ORG_SUBORDINADO IS NOT NULL 
            AND NOME_ORG_SUBORDINADO IS NOT NULL
    ) AS ORIGEM
        
    
    ON DESTINO.[ID_COD] = ORIGEM.[COD_ORG_SUBORDINADO]
        WHEN MATCHED 
            AND (DESTINO.NOME_ORG_SUBORDINADO <> ORIGEM.NOME_ORG_SUBORDINADO)
            AND DESTINO.ATIVO=1
        THEN
            UPDATE SET DESTINO.DATA_FIM = GETDATE(), DESTINO.ATIVO=0

        WHEN NOT MATCHED
        THEN
            INSERT (ID_COD, NOME_ORG_SUBORDINADO, DATA_INI, DATA_FIM, ATIVO) VALUES (ORIGEM.COD_ORG_SUBORDINADO, ORIGEM.NOME_ORG_SUBORDINADO, GETDATE(), NULL, 1)
        OUTPUT $action,
            ORIGEM.COD_ORG_SUBORDINADO,
            ORIGEM.NOME_ORG_SUBORDINADO,
            GETDATE(),
            NULL,
            1
)
as changes
(
    action,
    ID_COD,
    NOME_ORG_SUBORDINADO,
    DATA_INI,
    DATA_FIM,
    ATIVO
)
WHERE ACTION='UPDATE';
-- FIM MERGE

-- GRAVA LOG
INSERT INTO [DW_09].[LOGS].[LOG_CHALLENGE]
                ([NUMERO_ERRO],
                [SERVERIDADE_ERRO],
                [ESTADO_ERRO],
                [PROC_ERRO],
                [LINHA_ERRO],
                [MSG_ERRO],
                [SITUACAO],
                [PROCESSO],
                [DATA_INI],
                [DATA_FIM])
            VALUES
                (ERROR_NUMBER(),
                ERROR_SEVERITY(),
                ERROR_STATE(),
                ERROR_PROCEDURE(),
                ERROR_LINE(),
                ERROR_MESSAGE(),
                'SUCESSO',
                'CARGA DIMENSAO ORG SUBORDINADO',
                @VDATA_INI,
                GETDATE()
                )

IF @@TRANCOUNT > 0
        SELECT @@TRANCOUNT, 'Sucesso';
        COMMIT TRANSACTION;

END TRY

BEGIN CATCH
-- GRAVA LOG DE ERRO
    SELECT @@TRANCOUNT, 'ERRO';
    IF @@TRANCOUNT > 0
        ROLLBACK TRANSACTION;

INSERT INTO [DW_09].[LOGS].[LOG_CHALLENGE]
            ([NUMERO_ERRO],
            [SERVERIDADE_ERRO],
            [ESTADO_ERRO],
            [PROC_ERRO],
            [LINHA_ERRO],
            [MSG_ERRO],
            [SITUACAO],
            [PROCESSO],
            [DATA_INI],
            [DATA_FIM])
        VALUES
            (ERROR_NUMBER(),
            ERROR_SEVERITY(),
            ERROR_STATE(),
            ERROR_PROCEDURE(),
            ERROR_LINE(),
            ERROR_MESSAGE(),
            'ERRO',
            'CARGA DIMENSOES ORG SUBORDINADO',
            @VDATA_INI,
            GETDATE()
            )
END CATCH;

Commands completed successfully.

(0 rows affected)

(1 row affected)

(1 row affected)

Total execution time: 00:00:00.877

(No column name) (No column name) 1 Sucesso

**Carga Dimensao** D\_Unid\_Gestora

Na tabela STG\_CHALLENGE, existem nomes diferentes para o mesmo código, porém no merge a parte do "when matched" a verificação é feita uma vez antes de inserir a outra tabela.  
Então foi criado uma tabela temporária para passar a primeira linha que contenha o código da unidade gestora

In [ ]:
USE DW_09
GO

SELECT COD_UNID_GESTORA, NOME_UNID_GESTORA FROM [DW_09].[STAGING].[STG_CHALLENGE]

In [22]:
USE DW_09
GO

CREATE TABLE [DW_09].[#GESTORA](
    COD_UNID_GESTORA INT, 
    NOME_UNID_GESTORA NVARCHAR(250)
)
GO

-- TABELA PARTICIONADO PELO CÓDIGO DA UNIDADE
WITH ORG_GESTORA AS (
    SELECT DISTINCT RANK() OVER (PARTITION BY COD_UNID_GESTORA ORDER BY NOME_UNID_GESTORA ASC) 
    AS RANK_UNID_GESTORA, COD_UNID_GESTORA, NOME_UNID_GESTORA FROM [DW_09].[STAGING].[STG_CHALLENGE] 
        WHERE COD_UNID_GESTORA IS NOT NULL 
            AND NOME_UNID_GESTORA IS NOT NULL)

-- INSERIDO NA TABELA TEMPORÁRIA APENAS O PRIMEIRO RESULTADO DE CADA PARTIÇÃO DA TABELA SUPERIOR
INSERT INTO [DW_09].[#GESTORA](COD_UNID_GESTORA, NOME_UNID_GESTORA) 
SELECT COD_UNID_GESTORA, NOME_UNID_GESTORA FROM ORG_GESTORA WHERE RANK_UNID_GESTORA = 1

Commands completed successfully.

Commands completed successfully.

(3323 rows affected)

Total execution time: 00:00:00.764

In [23]:
USE DW_09
GO

BEGIN TRANSACTION;
    DECLARE @VDATA_INI DATETIME;
    SET @VDATA_INI= GETDATE();

BEGIN TRY

-- INICIA MERGE
INSERT INTO [DW_09].[SILVER].[D_Unid_Gestora](ID_COD, NOME_UNID_GESTORA, DATA_INI, DATA_FIM, ATIVO)
SELECT ID_COD, NOME_UNID_GESTORA, DATA_INI, DATA_FIM, ATIVO
FROM (
    MERGE [DW_09].[SILVER].[D_Unid_Gestora] AS DESTINO 
    
    USING (
        SELECT COD_UNID_GESTORA, NOME_UNID_GESTORA FROM [DW_09].[#GESTORA]
    ) AS ORIGEM
    
    ON DESTINO.[ID_COD] = ORIGEM.[COD_UNID_GESTORA]
        WHEN MATCHED 
            AND (DESTINO.NOME_UNID_GESTORA <> ORIGEM.NOME_UNID_GESTORA)
            AND DESTINO.ATIVO=1
        THEN
            UPDATE SET DESTINO.DATA_FIM = GETDATE()

        WHEN NOT MATCHED
        THEN
            INSERT (ID_COD, NOME_UNID_GESTORA, DATA_INI, DATA_FIM, ATIVO) VALUES (ORIGEM.COD_UNID_GESTORA, ORIGEM.NOME_UNID_GESTORA, GETDATE(), NULL, 1)
        OUTPUT $action,
            ORIGEM.COD_UNID_GESTORA,
            ORIGEM.NOME_UNID_GESTORA,
            GETDATE(),
            NULL,
            1
)
as changes
(
    action,
    ID_COD,
    NOME_UNID_GESTORA,
    DATA_INI,
    DATA_FIM,
    ATIVO
)
WHERE ACTION='UPDATE';
-- FIM MERGE

-- GRAVA LOG
INSERT INTO [DW_09].[LOGS].[LOG_CHALLENGE]
                ([NUMERO_ERRO],
                [SERVERIDADE_ERRO],
                [ESTADO_ERRO],
                [PROC_ERRO],
                [LINHA_ERRO],
                [MSG_ERRO],
                [SITUACAO],
                [PROCESSO],
                [DATA_INI],
                [DATA_FIM])
            VALUES
                (ERROR_NUMBER(),
                ERROR_SEVERITY(),
                ERROR_STATE(),
                ERROR_PROCEDURE(),
                ERROR_LINE(),
                ERROR_MESSAGE(),
                'SUCESSO',
                'CARGA DIMENSAO UNID GESTORA',
                @VDATA_INI,
                GETDATE()
                )

IF @@TRANCOUNT > 0
        SELECT @@TRANCOUNT, 'Sucesso';
        COMMIT TRANSACTION;

END TRY

BEGIN CATCH
-- GRAVA LOG DE ERRO
    SELECT @@TRANCOUNT, 'ERRO';
    IF @@TRANCOUNT > 0
        ROLLBACK TRANSACTION;

INSERT INTO [DW_09].[LOGS].[LOG_CHALLENGE]
            ([NUMERO_ERRO],
            [SERVERIDADE_ERRO],
            [ESTADO_ERRO],
            [PROC_ERRO],
            [LINHA_ERRO],
            [MSG_ERRO],
            [SITUACAO],
            [PROCESSO],
            [DATA_INI],
            [DATA_FIM])
        VALUES
            (ERROR_NUMBER(),
            ERROR_SEVERITY(),
            ERROR_STATE(),
            ERROR_PROCEDURE(),
            ERROR_LINE(),
            ERROR_MESSAGE(),
            'ERRO',
            'CARGA DIMENSOES UNID GESTORA',
            @VDATA_INI,
            GETDATE()
            )
END CATCH;

Commands completed successfully.

(0 rows affected)

(1 row affected)

(1 row affected)

Total execution time: 00:00:00.389

(No column name) (No column name) 1 Sucesso

**Carga Dimensao** D\_Gestao

In [24]:
USE DW_09
GO

BEGIN TRANSACTION;
    DECLARE @VDATA_INI DATETIME;
    SET @VDATA_INI= GETDATE();

BEGIN TRY
-- INICIA MERGE
INSERT INTO [DW_09].[SILVER].[D_Gestao](ID_COD, NOME_GESTAO, DATA_INI, DATA_FIM, ATIVO)
SELECT ID_COD, NOME_GESTAO, DATA_INI, DATA_FIM, ATIVO
FROM (
    MERGE [DW_09].[SILVER].[D_Gestao] AS DESTINO 
    
    USING (
        SELECT DISTINCT COD_GESTAO, NOME_GESTAO
        FROM [DW_09].[STAGING].[STG_CHALLENGE] 
        WHERE COD_GESTAO IS NOT NULL 
            AND NOME_GESTAO IS NOT NULL
    ) AS ORIGEM
    
    ON DESTINO.[ID_COD] = ORIGEM.[COD_GESTAO]
        WHEN MATCHED 
            AND (DESTINO.NOME_GESTAO <> ORIGEM.NOME_GESTAO)
            AND DESTINO.ATIVO=1
        THEN
            UPDATE SET DESTINO.DATA_FIM = GETDATE(), DESTINO.ATIVO=0

        WHEN NOT MATCHED
        THEN
            INSERT (ID_COD, NOME_GESTAO, DATA_INI, DATA_FIM, ATIVO) VALUES (ORIGEM.COD_GESTAO, ORIGEM.NOME_GESTAO, GETDATE(), NULL, 1)
        OUTPUT $action,
            ORIGEM.COD_GESTAO,
            ORIGEM.NOME_GESTAO,
            GETDATE(),
            NULL,
            1
)
as changes
(
    action,
    ID_COD,
    NOME_GESTAO,
    DATA_INI,
    DATA_FIM,
    ATIVO
)
WHERE ACTION='UPDATE';
-- FIM DO MERGE

-- GRAVA LOG
INSERT INTO [DW_09].[LOGS].[LOG_CHALLENGE]
                ([NUMERO_ERRO],
                [SERVERIDADE_ERRO],
                [ESTADO_ERRO],
                [PROC_ERRO],
                [LINHA_ERRO],
                [MSG_ERRO],
                [SITUACAO],
                [PROCESSO],
                [DATA_INI],
                [DATA_FIM])
            VALUES
                (ERROR_NUMBER(),
                ERROR_SEVERITY(),
                ERROR_STATE(),
                ERROR_PROCEDURE(),
                ERROR_LINE(),
                ERROR_MESSAGE(),
                'SUCESSO',
                'CARGA DIMENSAO GESTAO',
                @VDATA_INI,
                GETDATE()
                )

IF @@TRANCOUNT > 0
        SELECT @@TRANCOUNT, 'Sucesso';
        COMMIT TRANSACTION;

END TRY

BEGIN CATCH
-- GRAVA LOG DE ERRO
    SELECT @@TRANCOUNT, 'ERRO';
    IF @@TRANCOUNT > 0
        ROLLBACK TRANSACTION;

INSERT INTO [DW_09].[LOGS].[LOG_CHALLENGE]
            ([NUMERO_ERRO],
            [SERVERIDADE_ERRO],
            [ESTADO_ERRO],
            [PROC_ERRO],
            [LINHA_ERRO],
            [MSG_ERRO],
            [SITUACAO],
            [PROCESSO],
            [DATA_INI],
            [DATA_FIM])
        VALUES
            (ERROR_NUMBER(),
            ERROR_SEVERITY(),
            ERROR_STATE(),
            ERROR_PROCEDURE(),
            ERROR_LINE(),
            ERROR_MESSAGE(),
            'ERRO',
            'CARGA DIMENSOES GESTAO',
            @VDATA_INI,
            GETDATE()
            )
END CATCH;

Commands completed successfully.

(0 rows affected)

(1 row affected)

(1 row affected)

Total execution time: 00:00:00.580

(No column name) (No column name) 1 Sucesso

**Carga Dimensao** D\_Grp\_Despesa

In [25]:
USE DW_09
GO

BEGIN TRANSACTION;
    DECLARE @VDATA_INI DATETIME;
    SET @VDATA_INI= GETDATE();

BEGIN TRY
-- INICIA MERGE
INSERT INTO [DW_09].[SILVER].[D_Grp_Despesa](ID_COD, NOME_GRP_DESPESA, DATA_INI, DATA_FIM, ATIVO)
SELECT ID_COD, NOME_GRP_DESPESA, DATA_INI, DATA_FIM, ATIVO
FROM (
    MERGE [DW_09].[SILVER].[D_Grp_Despesa] AS DESTINO 
    
    USING (
        SELECT DISTINCT COD_GRP_DESPESA, NOME_GRP_DESPESA
        FROM [DW_09].[STAGING].[STG_CHALLENGE] 
        WHERE COD_GRP_DESPESA IS NOT NULL 
            AND NOME_GRP_DESPESA IS NOT NULL
    ) AS ORIGEM
    
    ON DESTINO.[ID_COD] = ORIGEM.[COD_GRP_DESPESA]
        WHEN MATCHED 
            AND (DESTINO.NOME_GRP_DESPESA <> ORIGEM.NOME_GRP_DESPESA)
            AND DESTINO.ATIVO=1
        THEN
            UPDATE SET DESTINO.DATA_FIM = GETDATE(), DESTINO.ATIVO=0

        WHEN NOT MATCHED
        THEN
            INSERT (ID_COD, NOME_GRP_DESPESA, DATA_INI, DATA_FIM, ATIVO) VALUES (ORIGEM.COD_GRP_DESPESA, ORIGEM.NOME_GRP_DESPESA, GETDATE(), NULL, 1)
        OUTPUT $action,
            ORIGEM.COD_GRP_DESPESA,
            ORIGEM.NOME_GRP_DESPESA,
            GETDATE(),
            NULL,
            1
)
as changes
(
    action,
    ID_COD,
    NOME_GRP_DESPESA,
    DATA_INI,
    DATA_FIM,
    ATIVO
)
WHERE ACTION='UPDATE';
-- TERMINA MERGE

-- GRAVA LOG
INSERT INTO [DW_09].[LOGS].[LOG_CHALLENGE]
                ([NUMERO_ERRO],
                [SERVERIDADE_ERRO],
                [ESTADO_ERRO],
                [PROC_ERRO],
                [LINHA_ERRO],
                [MSG_ERRO],
                [SITUACAO],
                [PROCESSO],
                [DATA_INI],
                [DATA_FIM])
            VALUES
                (ERROR_NUMBER(),
                ERROR_SEVERITY(),
                ERROR_STATE(),
                ERROR_PROCEDURE(),
                ERROR_LINE(),
                ERROR_MESSAGE(),
                'SUCESSO',
                'CARGA DIMENSAO GRP DESPESA',
                @VDATA_INI,
                GETDATE()
                )

IF @@TRANCOUNT > 0
        SELECT @@TRANCOUNT, 'Sucesso';
        COMMIT TRANSACTION;

END TRY

BEGIN CATCH
-- GRAVA LOG DE ERRO
    SELECT @@TRANCOUNT, 'ERRO';
    IF @@TRANCOUNT > 0
        ROLLBACK TRANSACTION;

INSERT INTO [DW_09].[LOGS].[LOG_CHALLENGE]
            ([NUMERO_ERRO],
            [SERVERIDADE_ERRO],
            [ESTADO_ERRO],
            [PROC_ERRO],
            [LINHA_ERRO],
            [MSG_ERRO],
            [SITUACAO],
            [PROCESSO],
            [DATA_INI],
            [DATA_FIM])
        VALUES
            (ERROR_NUMBER(),
            ERROR_SEVERITY(),
            ERROR_STATE(),
            ERROR_PROCEDURE(),
            ERROR_LINE(),
            ERROR_MESSAGE(),
            'ERRO',
            'CARGA DIMENSOES GRP DESPESA',
            @VDATA_INI,
            GETDATE()
            )
END CATCH;

Commands completed successfully.

(0 rows affected)

(1 row affected)

(1 row affected)

Total execution time: 00:00:00.497

(No column name) (No column name) 1 Sucesso

**Criação tabela Fato**

- F\_Despesa | Tabela fato conforme o pedido para análise das despesas
    - SK\_TRANSACAO| código SK da transação || INT, NOT NULL, AUTO INCREMENT
    - DATA\_MES | Data da Despesa || DATATIME, NOT NULL, 
    - SK\_ORG\_SUPERIOR | código SK do Órgão Superior || INT, NOT NULL, UNIQUE, 
    - SK\_ORG\_SUBORDINADO | código SK do Órgão Subordinado || INT, NOT NULL, UNIQUE, 
    - SK\_UNID\_GESTORA | código SK da Unidade Gestora || INT, NOT NULL, UNIQUE, 
    - SK\_GESTAO | código SK da Gestão || INT, NOT NULL, UNIQUE, 
    - SK\_GRP\_DESPESA | código SK do Grupo de Despesa || INT, NOT NULL, UNIQUE, 
    - VALOR\_EMPENHADO | Valor Empenhado || DECIMAL(15,2), NOT NULL, 
    - VALOR\_LIQUIDADO | Valor Liquidado || DECIMAL(15,2), NOT NULL, 
    - VALOR\_PAGO | Valor Pago || DECIMAL(15,2), NOT NULL)

In [26]:
USE DW_09
GO

IF NOT EXISTS (SELECT * FROM sysobjects WHERE name='F_Despesa' AND xtype='U')

CREATE TABLE [DW_09].[GOLD].[F_Despesa]
(
    [SK_TRANSACAO] INT IDENTITY(1,1) NOT NULL,
    [DATA_MES] DATETIME NOT NULL,
    [SK_ORG_SUPERIOR] INT NOT NULL,
    [SK_ORG_SUBORDINADO] INT NOT NULL,
    [SK_UNID_GESTORA] INT NOT NULL,
    [SK_GESTAO] INT NOT NULL,
    [SK_GRP_DESPESA] INT NOT NULL,
    [VALOR_EMPENHADO] DECIMAL(15,2) NOT NULL,
    [VALOR_LIQUIDADO] DECIMAL(15,2) NOT NULL,
    [VALOR_PAGO] DECIMAL(15,2) NOT NULL

    PRIMARY KEY CLUSTERED([SK_TRANSACAO] ASC) 
        WITH (PAD_INDEX = OFF, STATISTICS_NORECOMPUTE = OFF, IGNORE_DUP_KEY = OFF, ALLOW_ROW_LOCKS = ON, ALLOW_PAGE_LOCKS = ON, OPTIMIZE_FOR_SEQUENTIAL_KEY = OFF) ON [PRIMARY]
) ON [PRIMARY]
GO

Commands completed successfully.

Commands completed successfully.

Total execution time: 00:00:00.324

**Truncando Tabela Fato**

In [27]:
USE DW_09
GO

TRUNCATE TABLE [DW_09].[GOLD].[F_Despesa]
GO

Commands completed successfully.

Commands completed successfully.

Total execution time: 00:00:00.330

**Analisando amostragem dos dados**

In [28]:
USE DW_09
GO

SELECT
        STG_ORIGRM.ANO_MES,
        ORG_SUPERIOR.SK_ORG_SUPERIOR,
        ORG_SUBORDINADO.SK_ORG_SUBORDINADO,
        UNID_GESTORA.SK_UNID_GESTORA,
        GESTAO.SK_GESTAO,
        GRP_DESPESA.SK_GRP_DESPESA,
        STG_ORIGRM.VALOR_EMPENHADO,
        STG_ORIGRM.VALOR_LIQUIDADO,
        STG_ORIGRM.VALOR_PAGO

    FROM [DW_09].[STAGING].[STG_CHALLENGE] STG_ORIGRM
    INNER JOIN [DW_09].[SILVER].[D_Org_Superior] ORG_SUPERIOR
    ON STG_ORIGRM.COD_ORG_SUPERIOR = ORG_SUPERIOR.ID_COD
    AND ORG_SUPERIOR.ATIVO=1

    INNER JOIN [DW_09].[SILVER].[D_Org_Subordinado] ORG_SUBORDINADO
    ON STG_ORIGRM.COD_ORG_SUBORDINADO = ORG_SUBORDINADO.ID_COD
    AND ORG_SUBORDINADO.ATIVO=1

    INNER JOIN [DW_09].[SILVER].[D_Unid_Gestora] UNID_GESTORA
    ON STG_ORIGRM.COD_UNID_GESTORA = UNID_GESTORA.ID_COD
    AND UNID_GESTORA.ATIVO=1

    INNER JOIN [DW_09].[SILVER].[D_Gestao] GESTAO
    ON STG_ORIGRM.COD_GESTAO = GESTAO.ID_COD
    AND GESTAO.ATIVO=1

    INNER JOIN [DW_09].[SILVER].[D_Grp_Despesa] GRP_DESPESA
    ON STG_ORIGRM.COD_GRP_DESPESA = GRP_DESPESA.ID_COD
    AND GRP_DESPESA.ATIVO=1 

GO

Commands completed successfully.

(139995 rows affected)

Displaying Top 5000 rows.

Total execution time: 00:00:02.391

ANO_MES SK_ORG_SUPERIOR SK_ORG_SUBORDINADO SK_UNID_GESTORA SK_GESTAO SK_GRP_DESPESA VALOR_EMPENHADO VALOR_LIQUIDADO VALOR_PAGO 2022/01/01 5 31 1483 169 5 0.0000 0.0000 0.0000 2022/01/01 2 19 2076 169 5 0.0000 0.0000 0.0000 2022/01/01 16 181 507 186 5 5972.0000 5972.0000 5972.0000 2022/01/01 16 12 870 91 5 0.0000 0.0000 0.0000 2022/01/01 16 91 1199 162 3 175000.0000 36064.4100 0.0000 2022/01/01 5 123 3289 169 1 0.0000 0.0000 0.0000 2022/01/01 2 39 67 168 5 0.0000 0.0000 0.0000 2022/01/01 16 111 1004 183 5 276.4900 276.4900 276.4900 2022/01/01 15 189 2230 138 1 0.0000 0.0000 0.0000 2022/01/01 16 110 1192 130 5 500.0000 0.0000 0.0000 2022/01/01 19 175 2564 169 5 59700.0000 0.0000 0.0000 2022/01/01 2 19 2102 169 5 20.0000 0.0000 0.0000 2022/01/01 2 19 2040 169 3 2434000.0000 2156944.7000 1010618.7500 2022/01/01 15 189 2251 138 5 0.0000 0.0000 0.0000 2022/01/01 13 33 231 152 5 850.0000 850.0000 93.5000 2022/01/01 16 110 971 130 5 5542.0700 5542.0700 5542.0700 2022/01/01 18 18 3140 169 5 34545.6100 0.0000 0.0000 2022/01/01 16 49 740 9 5 0.0600 0.0600 0.0600 2022/01/01 16 133 860 177 3 360000.0000 30969.1700 30969.1700 2022/01/01 1 113 2171 169 1 0.0000 0.0000 0.0000 2022/01/01 19 95 2576 51 3 15000.0000 3190.1100 0.0000 2022/01/01 16 228 459 136 5 500.0000 500.0000 500.0000 2022/01/01 16 134 460 88 5 0.0000 0.0000 0.0000 2022/01/01 1 32 2689 72 5 151338.4400 146153.0700 45614.8000 2022/01/01 3 217 2169 145 5 0.0000 0.0000 0.0000 2022/01/01 16 181 507 186 5 630000.0000 17301.4100 14005.1600 2022/01/01 14 184 2877 116 5 0.0000 0.0000 0.0000 2022/01/01 4 122 2710 172 5 1032932.3900 0.0000 0.0000 2022/01/01 11 83 2523 169 5 0.0000 0.0000 0.0000 2022/01/01 2 19 2056 169 5 0.0000 0.0000 0.0000 2022/01/01 5 31 1398 169 5 0.0000 0.0000 0.0000 2022/01/01 16 157 708 75 3 980956103.0700 69973.4900 69973.4900 2022/01/01 19 69 2595 133 5 0.0000 0.0000 0.0000 2022/01/01 5 123 3233 169 3 630000.0000 30749.6400 0.0000 2022/01/01 5 123 3290 169 5 0.0000 0.0000 0.0000 2022/01/01 16 51 935 18 5 0.0000 0.0000 0.0000 2022/01/01 19 69 2596 133 5 5000.0000 0.0000 0.0000 2022/01/01 4 153 2950 59 5 0.0000 0.0000 0.0000 2022/01/01 13 138 165 169 5 1787.3300 0.0000 0.0000 2022/01/01 16 111 807 183 5 2120.2800 0.0000 0.0000 2022/01/01 16 27 535 77 5 443.4700 443.4700 0.0000 2022/01/01 5 151 91 169 3 0.0000 0.0000 0.0000 2022/01/01 1 156 2185 50 3 1222889.3400 1222889.3400 1222889.3400 2022/01/01 16 229 465 87 5 13010.0000 0.0000 0.0000 2022/01/01 10 53 3002 28 5 0.0000 0.0000 0.0000 2022/01/01 16 237 881 48 3 50000.0000 2352.8000 2352.8000 2022/01/01 16 50 1213 118 5 0.0000 0.0000 0.0000 2022/01/01 5 31 1577 169 5 1228.0200 1228.0200 0.0000 2022/01/01 2 19 2117 169 5 0.0000 0.0000 0.0000 2022/01/01 2 39 69 168 5 0.0000 0.0000 0.0000 2022/01/01 13 233 2790 132 5 0.0000 0.0000 0.0000 2022/01/01 15 155 2297 169 5 3000.0000 0.0000 0.0000 2022/01/01 16 88 829 30 5 0.0000 0.0000 0.0000 2022/01/01 16 157 824 75 5 0.0000 0.0000 0.0000 2022/01/01 16 70 637 101 3 79038598.0000 9019110.2300 0.0000 2022/01/01 16 111 841 183 5 0.0000 0.0000 0.0000 2022/01/01 17 227 2739 78 5 1295.5600 1295.5600 0.0000 2022/01/01 16 157 736 75 5 0.0000 0.0000 0.0000 2022/01/01 4 37 2731 65 5 727774.0000 48680.4600 0.0000 2022/01/01 16 107 664 44 5 0.0000 0.0000 0.0000 2022/01/01 15 189 2248 138 5 0.0000 0.0000 0.0000 2022/01/01 5 77 2035 36 5 832762.1600 0.0000 0.0000 2022/01/01 16 70 637 101 5 1097000.0000 852092.8800 850891.2800 2022/01/01 5 165 1969 169 5 0.0000 0.0000 0.0000 2022/01/01 15 34 2357 169 5 60480.5000 0.0000 0.0000 2022/01/01 10 53 2965 28 5 3.0000 0.0000 0.0000 2022/01/01 13 33 391 152 5 0.0000 0.0000 0.0000 2022/01/01 10 53 2969 28 5 3327.5000 0.0000 0.0000 2022/01/01 7 205 2492 169 5 0.0000 0.0000 0.0000 2022/01/01 2 152 2167 179 5 140560.6400 140992.2700 0.0000 2022/01/01 2 39 60 168 5 0.0000 0.0000 0.0000 2022/01/01 5 139 16 169 5 10000.0000 0.0000 0.0000 2022/01/01 2 19 2155 169 5 100000.0000 27303.7000 27303.7000 2022/01/01 2 19 2089 169 5 10.0000 0.0000 0.0000 2022/0

**Carga tabela Fato**

In [29]:
USE DW_09
GO

BEGIN TRANSACTION;
    DECLARE @VDATA_INI DATETIME;
    DECLARE @VPROCESSO VARCHAR(30);
    SET @VDATA_INI= GETDATE();
    SET @VPROCESSO= 'CARGA FATO'

BEGIN TRY
-- INICIA MERGE
MERGE [DW_09].[GOLD].[F_Despesa] AS DESTINO

USING (
    SELECT
        TRY_CONVERT(DATE, STG_ORIGRM.ANO_MES, 111) AS ANO_MES, -- CONVERTENDO O NVARCHAR PARA DATATIME
        ORG_SUPERIOR.SK_ORG_SUPERIOR,
        ORG_SUBORDINADO.SK_ORG_SUBORDINADO,
        UNID_GESTORA.SK_UNID_GESTORA,
        GESTAO.SK_GESTAO,
        GRP_DESPESA.SK_GRP_DESPESA,
        TRY_CONVERT(DECIMAL(15,2), STG_ORIGRM.VALOR_EMPENHADO) AS VALOR_EMPENHADO, -- CONVERTENDO NVARCHAR PARA DECIMAL
        TRY_CONVERT(DECIMAL(15,2), STG_ORIGRM.VALOR_LIQUIDADO) AS  VALOR_LIQUIDADO, -- CONVERTENDO NVARCHAR PARA DECIMAL
        TRY_CONVERT(DECIMAL(15,2), STG_ORIGRM.VALOR_PAGO) AS VALOR_PAGO -- CONVERTENDO NVARCHAR PARA DECIMAL

    FROM [DW_09].[STAGING].[STG_CHALLENGE] STG_ORIGRM
    INNER JOIN DW_09.SILVER.D_Org_Superior ORG_SUPERIOR
    ON STG_ORIGRM.COD_ORG_SUPERIOR = ORG_SUPERIOR.ID_COD
    AND ORG_SUPERIOR.ATIVO=1

    INNER JOIN [DW_09].[SILVER].[D_Org_Subordinado] ORG_SUBORDINADO
    ON STG_ORIGRM.COD_ORG_SUBORDINADO = ORG_SUBORDINADO.ID_COD
    AND ORG_SUBORDINADO.ATIVO=1

    INNER JOIN [DW_09].[SILVER].[D_Unid_Gestora] UNID_GESTORA
    ON STG_ORIGRM.COD_UNID_GESTORA = UNID_GESTORA.ID_COD
    AND UNID_GESTORA.ATIVO=1

    INNER JOIN [DW_09].[SILVER].[D_Gestao] GESTAO
    ON STG_ORIGRM.COD_GESTAO = GESTAO.ID_COD
    AND GESTAO.ATIVO=1

    INNER JOIN [DW_09].[SILVER].[D_Grp_Despesa] GRP_DESPESA
    ON STG_ORIGRM.COD_GRP_DESPESA = GRP_DESPESA.ID_COD
    AND GRP_DESPESA.ATIVO=1 
    
    WHERE ANO_MES IS NOT NULL 
        AND VALOR_EMPENHADO IS NOT NULL
        AND VALOR_LIQUIDADO IS NOT NULL
        AND VALOR_PAGO IS NOT NULL
    ) AS ORIGEM

    ON (DESTINO.SK_GESTAO = ORIGEM.SK_GESTAO AND DESTINO.SK_GRP_DESPESA = ORIGEM.SK_GRP_DESPESA)

    WHEN MATCHED
    -- SE HÁ REGISTRO NO DESTINO, ATUALIZE
    THEN UPDATE SET
        DATA_MES = ORIGEM.ANO_MES,
        SK_ORG_SUPERIOR = ORIGEM.SK_ORG_SUPERIOR,
        SK_ORG_SUBORDINADO = ORIGEM.SK_ORG_SUBORDINADO,
        SK_UNID_GESTORA = ORIGEM.SK_UNID_GESTORA,
        SK_GESTAO = ORIGEM.SK_GESTAO,
        SK_GRP_DESPESA = ORIGEM.SK_GRP_DESPESA,
        VALOR_EMPENHADO = ORIGEM.VALOR_EMPENHADO,
        VALOR_LIQUIDADO = ORIGEM.VALOR_LIQUIDADO,
        VALOR_PAGO = ORIGEM.VALOR_PAGO

    WHEN NOT MATCHED
    -- QUANDO NÃO HÁ, INSERIR O DADO
    THEN INSERT (DATA_MES, SK_ORG_SUPERIOR, SK_ORG_SUBORDINADO, SK_UNID_GESTORA, SK_GESTAO, SK_GRP_DESPESA, VALOR_EMPENHADO, VALOR_LIQUIDADO, VALOR_PAGO)
        VALUES(
            ORIGEM.ANO_MES,
            ORIGEM.SK_ORG_SUPERIOR,
            ORIGEM.SK_ORG_SUBORDINADO,
            ORIGEM.SK_UNID_GESTORA,
            ORIGEM.SK_GESTAO,
            ORIGEM.SK_GRP_DESPESA,
            ORIGEM.VALOR_EMPENHADO,
            ORIGEM.VALOR_LIQUIDADO,
            ORIGEM.VALOR_PAGO
        );
--FIM MERGE

--GRAVA LOG
INSERT INTO [DW_09].[LOGS].[LOG_CHALLENGE]

([NUMERO_ERRO],
           [SERVERIDADE_ERRO],
           [ESTADO_ERRO],
           [PROC_ERRO],
           [LINHA_ERRO],
           [MSG_ERRO],
           [SITUACAO],
           [PROCESSO],
           [DATA_INI],
		   [DATA_FIM])
     VALUES
        (ERROR_NUMBER(),
        ERROR_SEVERITY(),
        ERROR_STATE(),
        ERROR_PROCEDURE(),
        ERROR_LINE() ,
        ERROR_MESSAGE() ,
        'SUCESSO',
        @VPROCESSO,
		@VDATA_INI,
		GETDATE()
		)
SELECT 'SUCESSO ANTES',@@TRANCOUNT
IF @@TRANCOUNT > 0  
    COMMIT TRANSACTION;  
SELECT 'SUCESSO DEPOIS',@@TRANCOUNT    
END TRY  

BEGIN CATCH
-- GRAVA LOG DE ERRO
SELECT 'ERRO ANTES',@@TRANCOUNT    
 	IF @@TRANCOUNT > 0  
        ROLLBACK TRANSACTION; 
SELECT 'ERRO DEPOIS',@@TRANCOUNT    
INSERT INTO [DW_09].[LOGS].[LOG_CHALLENGE]
           ([NUMERO_ERRO],
           [SERVERIDADE_ERRO],
           [ESTADO_ERRO],
           [PROC_ERRO],
           [LINHA_ERRO],
           [MSG_ERRO],
           [SITUACAO],
           [PROCESSO],
           [DATA_INI],
		   [DATA_FIM])
     VALUES
        (ERROR_NUMBER(),
        ERROR_SEVERITY(),
        ERROR_STATE(),
        ERROR_PROCEDURE(),
        ERROR_LINE() ,
        ERROR_MESSAGE() ,
        'ERRO',
        @VPROCESSO,
		@VDATA_INI,
		GETDATE()
		)

END CATCH;

Commands completed successfully.

(139995 rows affected)

(1 row affected)

(1 row affected)

(1 row affected)

Total execution time: 00:00:01.438

(No column name) (No column name) SUCESSO ANTES 1

(No column name) (No column name) SUCESSO DEPOIS 0

**PROCESSO FINALIZADO**

In [30]:
USE DW_09
GO

SELECT TOP 50 
    FORMAT(DATA_MES, 'MM/yyyy') AS MES,
    SUPERIOR.NOME_ORG_SUPERIOR,  
    SUBORDINADO.NOME_ORG_SUBORDINADO,
    GESTORA.NOME_UNID_GESTORA,
    GESTAO.NOME_GESTAO,
    DESPESA.NOME_GRP_DESPESA,
    FORMAT(VALOR_EMPENHADO, 'C', 'pt-br') AS VALOR_EMPENHADO,
    FORMAT(VALOR_LIQUIDADO, 'C', 'pt-br') AS VALOR_LIQUIDADO,
    FORMAT(VALOR_PAGO, 'C', 'pt-br') AS VALOR_PAGO


    FROM [DW_09].[GOLD].[F_Despesa]
    INNER JOIN [DW_09].[SILVER].[D_Org_Superior] SUPERIOR ON [DW_09].[GOLD].[F_Despesa].SK_ORG_SUPERIOR = SUPERIOR.SK_ORG_SUPERIOR
    INNER JOIN [DW_09].[SILVER].[D_Org_Subordinado] SUBORDINADO ON [DW_09].[GOLD].[F_Despesa].SK_ORG_SUBORDINADO = SUBORDINADO.SK_ORG_SUBORDINADO
    INNER JOIN [DW_09].[SILVER].[D_Unid_Gestora] GESTORA ON [DW_09].[GOLD].[F_Despesa].SK_UNID_GESTORA = GESTORA.SK_UNID_GESTORA
    INNER JOIN [DW_09].[SILVER].[D_Gestao] GESTAO ON [DW_09].[GOLD].[F_Despesa].SK_GESTAO = GESTAO.SK_GESTAO
    INNER JOIN [DW_09].[SILVER].[D_Grp_Despesa] DESPESA ON [DW_09].[GOLD].[F_Despesa].SK_GRP_DESPESA = DESPESA.SK_GRP_DESPESA
GO

Commands completed successfully.

(50 rows affected)

Total execution time: 00:00:00.783

MES NOME_ORG_SUPERIOR NOME_ORG_SUBORDINADO NOME_UNID_GESTORA NOME_GESTAO NOME_GRP_DESPESA VALOR_EMPENHADO VALOR_LIQUIDADO VALOR_PAGO 03/2022 Ministério da Infraestrutura Departamento Nacional de Infraestrutura de Transportes DEPART.NAC.INFRA ESTRUTURA TRANSPORTES. DEPTO. NAC. DE INFRA±ESTRUTURA DE TRANSPORTES Outras Despesas Correntes R$ 2.000,00 R$ 4.005,63 R$ 67.631,88 03/2022 Ministério da Educação Universidade Federal de Campina Grande HOSPITAL UNIVERSITARIO ALCIDES CARNEIRO/UFCG UNIVERSIDADE FEDERAL DE CAMPINA GRANDE Pessoal e Encargos Sociais R$ 0,00 R$ 704.898,50 R$ 776.016,61 03/2022 Ministério da Defesa Comando da Aeronáutica GRUPAMENTO DE APOIO DE MANAUS TESOURO NACIONAL Outras Despesas Correntes R$ 0,00 R$ 0,00 R$ 0,00 03/2022 Ministério da Educação Universidade Federal da Paraíba UNIVERSIDADE FEDERAL DA PARAIBA UNIVERSIDADE FEDERAL DA PARAIBA Outras Despesas Correntes R$ 563.145,68 R$ 1.116.025,32 R$ 1.075.224,14 03/2022 Ministério do Trabalho Instituto Nacional do Seguro Social GERENCIA EXECUTIVA GOIANIA INSTITUTO NACIONAL DO SEGURO SOCIAL Outras Despesas Correntes R$ 9.995,51 R$ 9.995,51 R$ 9.995,51 03/2022 Ministério da Educação Empresa Brasileira de Serviços Hospitalares HOSPITAL UNIVERSITARIO DA UFJF EMPRESA BRASILEIRA DE SERVICOS HOSPITALARES Outras Despesas Correntes R$ 0,00 R$ 0,00 R$ 0,00 03/2022 Ministério da Defesa Comando do Exército COMANDO 7 REGIAO MILITAR/7 DIV DE EXERCITO TESOURO NACIONAL Outras Despesas Correntes R$ 0,00 R$ 41.722,24 R$ 41.722,24 03/2022 Ministério da Educação Universidade Federal do Espírito Santo UNIVERSIDADE FEDERAL DO ESPIRITO SANTO UNIVERSIDADE FEDERAL DO ESPIRITO SANTO Outras Despesas Correntes R$ 0,00 R$ 48.554,91 R$ 35.364,35 03/2022 Ministério da Defesa Comando do Exército 5º BATALHAO DE ENGENHARIA DE COMBATE BLINDADO TESOURO NACIONAL Outras Despesas Correntes R$ 0,00 R$ 0,00 R$ 0,00 03/2022 Ministério do Desenvolvimento Regional Companhia de Desenvolvimento dos Vales do São Francisco e do Parnaíba CIA DE DES.DOS VALES DO S.FRANC.E DO PARNAIBA CIA DE DESENV DOS VALES DO S.FRANC.E PARNAIBA Investimentos R$ 0,00 R$ 0,00 R$ 0,00 03/2022 Ministério da Educação Universidade Federal do Recôncavo da Bahia UNIVERSIDADE FEDERAL DO RECONCAVO DA BAHIA UNIVERSIDADE FEDERAL DO RECONCAVO DA BAHIA Outras Despesas Correntes R$ 0,00 R$ 0,00 R$ 967,24 03/2022 Ministério do Turismo Ministério do Turismo - Unidades com vínculo direto CAIXA - SNINFRA TESOURO NACIONAL Investimentos R$ 0,00 R$ 0,00 R$ 0,00 03/2022 Ministério da Educação Fundação Universidade do Maranhão FUNDACAO UNIVERSIDADE FEDERAL DO MARANHAO FUNDACAO UNIVERSIDADE DO MARANHAO Outras Despesas Correntes R$ 0,00 R$ 20.596,00 R$ 20.596,00 03/2022 Ministério da Defesa Comando do Exército 2 BATALHAO FERROVIARIO TESOURO NACIONAL Investimentos R$ 0,00 R$ 0,00 R$ 0,00 03/2022 Ministério do Trabalho Instituto Nacional do Seguro Social CGOFC REGIME PROPRIO DE PREV. SOCIAL INSTITUTO NACIONAL DO SEGURO SOCIAL Pessoal e Encargos Sociais R$ 270.000,00 R$ 44.758,23 R$ 0,00 03/2022 Ministério da Defesa Comando da Marinha ESCOLA DE APREND.-MARINHEIROS DE PERNAMBUCO TESOURO NACIONAL Outras Despesas Correntes R$ 27.403,46 R$ 23.684,71 R$ 881,25 03/2022 Ministério das Comunicações Empresa Brasil de Comunicação EMPRESA BRASIL DE COMUNICACAO S.A EMPRESA BRASIL DE COMUNICACAO Outras Despesas Correntes R$ 9.006,18 R$ 8.684,87 R$ 8.684,87 03/2022 Ministério da Defesa Fundo do Exército COMANDO DA 17 BRIGADA DE INFANTARIA DE SELVA TESOURO NACIONAL Outras Despesas Correntes R$ 1.251,74 R$ 1.251,74 R$ 1.251,74 03/2022 Ministério da Defesa Comando do Exército DEPARTAMENTO DE EDUCACAO E CULTURA DO EXERCIT TESOURO NACIONAL Outras Despesas Correntes R$ 0,00 R$ 0,00 R$ 0,00 03/2022 Ministério da Agricultura, Pecuária e Abastec Ministério da Agricultura, Pecuária e Abastecimento - Unidades com vínculo direto ASSESS. ESPEC. DE RELACOES GOVERN.E INSTITUC. TESOURO NACIONAL Investimentos R$ 0,00 R$ 0,00 R$ 0,00 03/2022 Ministério de Minas e Energia Companhia de Pesq

**<mark>\--- PARTE 2 - Conhecimentos de SQL e T-SQL(DML) ---</mark>**

1- Qual o total em Jan/2022 Valor Pago (R$) para cada Órgão Superior?

In [31]:
USE DW_09
GO

SELECT 
    FORMAT([F_Despesa].DATA_MES, 'MM/yyyy') AS MES, 
    SUPERIOR.ID_COD AS COD_ORG_SUPERIOR, 
    SUPERIOR.NOME_ORG_SUPERIOR, 
    FORMAT(SUM([F_Despesa].VALOR_PAGO), 'C', 'pt-br') AS VALOR_PAGO 

FROM [DW_09].[GOLD].[F_Despesa]
    INNER JOIN [DW_09].[SILVER].[D_Org_Superior] SUPERIOR ON [DW_09].[GOLD].[F_Despesa].SK_ORG_SUPERIOR = SUPERIOR.SK_ORG_SUPERIOR
    WHERE MONTH([F_Despesa].DATA_MES) = 1
    GROUP BY [F_Despesa].DATA_MES, SUPERIOR.ID_COD, SUPERIOR.NOME_ORG_SUPERIOR
    ORDER BY SUM([F_Despesa].VALOR_PAGO) ASC
GO

Commands completed successfully.

(21 rows affected)

Total execution time: 00:00:00.433

MES COD_ORG_SUPERIOR NOME_ORG_SUPERIOR VALOR_PAGO 01/2022 81000 Ministério da Mulher, Família e Direitos Huma R$ 1.642.643,67 01/2022 54000 Ministério do Turismo R$ 14.120.937,23 01/2022 25201 Banco Central do Brasil - Orçamento Fiscal e R$ 16.494.480,05 01/2022 41000 Ministério das Comunicações R$ 19.697.358,98 01/2022 20000 Presidência da República R$ 26.476.938,80 01/2022 37000 Controladoria-Geral da União R$ 28.666.971,67 01/2022 44000 Ministério do Meio Ambiente R$ 38.362.750,01 01/2022 39000 Ministério da Infraestrutura R$ 51.258.685,81 01/2022 24000 Ministério da Ciência, Tecnologia, Inovações R$ 91.194.010,90 01/2022 63000 Advocacia-Geral da União R$ 99.768.371,98 01/2022 22000 Ministério da Agricultura, Pecuária e Abastec R$ 160.075.783,08 01/2022 32000 Ministério de Minas e Energia R$ 184.691.860,89 01/2022 35000 Ministério das Relações Exteriores R$ 219.205.873,95 01/2022 30000 Ministério da Justiça e Segurança Pública R$ 347.220.150,34 01/2022 52000 Ministério da Defesa R$ 1.450.940.527,16 01/2022 53000 Ministério do Desenvolvimento Regional R$ 2.172.684.895,67 01/2022 26000 Ministério da Educação R$ 3.633.061.749,13 01/2022 36000 Ministério da Saúde R$ 5.921.404.686,18 01/2022 55000 Ministério da Cidadania R$ 7.172.552.844,52 01/2022 40000 Ministério do Trabalho R$ 21.858.285.755,09 01/2022 25000 Ministério da Economia R$ 234.311.147.177,06

2- Quais os top 10 Órgãos Superiores referente a Jan/2022 em Valor Pago (R$)

In [32]:
USE DW_09
GO

SELECT TOP 10 
    FORMAT([F_Despesa].DATA_MES, 'MM/yyyy') AS MES, 
    SUPERIOR.ID_COD AS COD_ORG_SUPERIOR, 
    SUPERIOR.NOME_ORG_SUPERIOR, 
    FORMAT(SUM([F_Despesa].VALOR_PAGO), 'C', 'pt-br') AS VALOR_PAGO 

FROM [DW_09].[GOLD].[F_Despesa]
    INNER JOIN [DW_09].[SILVER].[D_Org_Superior] SUPERIOR ON [DW_09].[GOLD].[F_Despesa].SK_ORG_SUPERIOR = SUPERIOR.SK_ORG_SUPERIOR
    WHERE MONTH([F_Despesa].DATA_MES) = 1
    GROUP BY [F_Despesa].DATA_MES, SUPERIOR.ID_COD, SUPERIOR.NOME_ORG_SUPERIOR
    ORDER BY SUM([F_Despesa].VALOR_PAGO) DESC
GO

Commands completed successfully.

(10 rows affected)

Total execution time: 00:00:00.367

MES COD_ORG_SUPERIOR NOME_ORG_SUPERIOR VALOR_PAGO 01/2022 25000 Ministério da Economia R$ 234.311.147.177,06 01/2022 40000 Ministério do Trabalho R$ 21.858.285.755,09 01/2022 55000 Ministério da Cidadania R$ 7.172.552.844,52 01/2022 36000 Ministério da Saúde R$ 5.921.404.686,18 01/2022 26000 Ministério da Educação R$ 3.633.061.749,13 01/2022 53000 Ministério do Desenvolvimento Regional R$ 2.172.684.895,67 01/2022 52000 Ministério da Defesa R$ 1.450.940.527,16 01/2022 30000 Ministério da Justiça e Segurança Pública R$ 347.220.150,34 01/2022 35000 Ministério das Relações Exteriores R$ 219.205.873,95 01/2022 32000 Ministério de Minas e Energia R$ 184.691.860,89

3- Qual o total no Trimestre do Valor Empenhado (R$) para cada Gestão?

In [33]:
USE DW_09
GO

SELECT 
    GESTAO.ID_COD AS COD_GESTAO, 
    GESTAO.NOME_GESTAO, 
    FORMAT(SUM([F_Despesa].VALOR_EMPENHADO), 'C', 'pt-br') AS VALOR_EMPENHADO 

FROM [DW_09].[GOLD].[F_Despesa]
    INNER JOIN [DW_09].[SILVER].[D_Gestao] GESTAO ON [DW_09].[GOLD].[F_Despesa].SK_GESTAO = GESTAO.SK_GESTAO
    GROUP BY GESTAO.ID_COD, GESTAO.NOME_GESTAO
    ORDER BY SUM([F_Despesa].VALOR_EMPENHADO) ASC
GO

Commands completed successfully.

(187 rows affected)

Total execution time: 00:00:00.352

COD_GESTAO NOME_GESTAO VALOR_EMPENHADO 19209 DEPTO. DE PATRIMONIO INDIGENA E MEIO AMBIENTE R$ 55.650,58 36801 FINANCIADORA DE ESTUDOS E PROJETOS R$ 85.014,47 26457 UNIVERSIDADE DO NORTE DO TOCANTINS R$ 604.160,00 12201 CAIXA DE FINANCIAMENTO IMOB. DA AERONAUTICA R$ 1.776.798,13 24290 FUNDACAO ALEXANDRE DE GUSMAO R$ 8.571.298,33 34208 FUNDACAO CULTURAL PALMARES R$ 9.973.708,23 53202 SUPERINTEND. DO DESENVOLVIMENTO DA AMAZONIA R$ 10.594.657,30 53203 SUPERINTENDENCIA DO DESENVOLV. DO NORDESTE R$ 10.993.757,89 24208 INSTITUTO NAC.DE TECNOLOGIA DA INFORMACAO±ITI R$ 12.701.680,01 20402 AGENCIA ESPACIAL BRASILEIRA - AEB R$ 14.229.026,20 26456 UNIVERSIDADE FEDERAL DO AGRESTE DE PERNAMBUCO R$ 14.548.336,16 53207 SUPERINT. DE DESENVOLVIMENTO DO CENTRO-OESTE R$ 18.133.687,80 26455 UNIVERSIDADE FEDERAL DO DELTA DO PARNAIBA R$ 20.390.618,24 30211 CONSELHO ADMINISTRATIVO DE DEFESA ECONOMICA R$ 22.036.821,47 16204 FUNDACAO OSORIO R$ 24.632.971,09 33206 SUPERINT.NACIONAL DE PREVIDENCIA COMPLEMENTAR R$ 28.069.367,76 24209 CENTRO NAC DE TECN ELETRONICA AVANCADA S/A R$ 32.844.460,60 42207 INSTITUTO BRASILEIRO DE MUSEUS R$ 35.507.841,78 26442 UNIV.DA INTEG.INTERN.DA LUSOF.AFRO-BRASILEIRA R$ 39.707.480,02 34201 FUNDACAO CASA DE RUI BARBOSA R$ 41.415.250,70 39253 EMPRESA DE PLANEJAMENTO E LOGISTICA S.A.- EPL R$ 41.446.764,99 26452 UNIVERSIDADE FEDERAL DE CATALAO R$ 43.863.180,87 26450 UNIVERSIDADE FEDERAL DO SUL DA BAHIA R$ 45.658.996,41 11401 FUNDACAO ESCOLA NACIONAL DE ADM. PUBLICA R$ 49.650.293,30 26415 INST.FED.DE EDUC.,CIENC.E TEC.DO MAT.G.DO SUL R$ 50.192.817,16 27208 EMPRESA DE TRENS URBANOS DE PORTO ALEGRE S/A R$ 52.299.463,33 44206 INSTITUTO DE PESQUISAS JARDIM BOTANICO DO RJ R$ 54.278.899,78 26437 INST.FED.DE EDUC.,CIENC.E TEC.DE RORAIMA R$ 56.365.897,47 26428 INST.FED.DE EDUC.,CIENC.E TEC.DE BRASILIA R$ 61.877.993,32 40402 FUNDACAO NACIONAL DE ARTES R$ 63.482.945,10 26425 INST.FED.DE EDUC.,CIENC.E TEC.DO ACRE R$ 64.273.984,57 26423 INST.FED.DE EDUC.,CIENC.E TEC.DE SERGIPE R$ 66.512.035,24 26352 FUNDACAO UNIVERSIDADE FEDERAL DO ABC R$ 70.908.857,13 26267 UNIVERS. FEDERAL DA INTEG. LATINO AMERICANA R$ 73.926.011,40 34209 BIBLIOTECA NACIONAL R$ 76.096.064,79 26454 UNIVERSIDADE FEDERAL DE RONDONOPOLIS R$ 81.413.319,63 26426 INST.FED.DE EDUC.,CIENC.E TEC.DO AMAPA R$ 87.678.785,07 26201 FUNDACAO JORGE DUPRAT FIG.SEG.MED.TRABALHO R$ 87.813.441,15 26440 UNIVERSIDADE FEDERAL DA FRONTEIRA SUL R$ 90.394.473,22 26449 UNIVERSIDADE FEDERAL DO CARIRI R$ 93.204.206,11 26453 UNIVERSIDADE FEDERAL DE JATAI R$ 93.323.818,39 32314 EMPRESA DE PESQUISA ENERGETICA R$ 96.509.288,07 26447 UNIVERSIDADE FEDERAL DO OESTE DA BAHIA R$ 96.998.937,71 20203 ANCINE-AGENCIA NACIONAL DO CINEMA R$ 101.013.161,14 26424 INST.FED.DE EDUC.,CIENC.E TEC.DO TOCANTINS R$ 107.858.833,19 15277 UNIVERSIDADE FEDERAL DE RORAIMA R$ 110.011.116,11 34202 FUNDACAO JOAQUIM NABUCO R$ 110.861.886,16 26436 INST.FED.DE EDUC.,CIE.E TEC.SUL-RIO-GRANDENSE R$ 111.405.737,07 15254 FUNDACAO UNIVERSIDADE FEDERAL DE RONDONIA R$ 120.621.056,49 16501 INDUSTRIA DE MATERIAL BELICO DO BRASIL R$ 122.025.288,93 26448 UNIVERSIDADE FEDERAL DO SUL E SUDESTE DO PARA R$ 124.712.041,97 68201 AGENCIA NACIONAL DE TRANSPORTES AQUAVIARIOS R$ 126.059.431,74 29208 COMPANHIA DE PESQUISA DE RECURSOS MINERAIS R$ 127.696.771,22 19205 SUPERINTENDENCIA DA ZONA FRANCA DE MANAUS R$ 129.423.023,66 15270 FUN.UNIV.FED.DE CIENCIAS DA SAUDE DE P.ALEGRE R$ 135.922.787,92 44207 INST.CHICO MENDES DE CONSER.DA BIODIVERSIDADE R$ 144.577.570,46 26430 INST.FED.DE ED.,CIENC.E TEC.DO S.PERNAMBUCANO R$ 150.716.476,89 15266 FUNDACAO UNIVERSIDADE FEDERAL DE SAO CARLOS R$ 156.251.752,27 18205 INSTIT.NAC. DE METROL. QUALID. E TECNOLOGIA R$ 158.139.433,55 26290 INSTITUTO NACIONAL DE EST.E PESQ.EDUCACIONAIS R$ 159.111.153,71 11203 DEPARTAMENTO NAC. DE OBRAS CONTRA AS SECAS R$ 170.553.290,82 26441 UNIVERSIDADE FEDERAL DO OESTE DO PARA R$ 174.543.299,13 26405 INST.FED.DE EDUC.,CIENC.E TEC.DO CEARA R$ 178.392.966,60 15278 FUNDACAO UNIVERSIDADE FEDERAL DO

4- Quais as Top 10 Gestão no Trimestre referente a valor empenhado?

In [34]:
USE DW_09
GO

SELECT TOP 10 
    GESTAO.ID_COD AS COD_GESTAO, 
    GESTAO.NOME_GESTAO, 
    FORMAT(SUM([F_Despesa].VALOR_EMPENHADO), 'C', 'pt-br') AS VALOR_EMPENHADO 

FROM [DW_09].[GOLD].[F_Despesa]
    INNER JOIN [DW_09].[SILVER].[D_Gestao] GESTAO ON [DW_09].[GOLD].[F_Despesa].SK_GESTAO = GESTAO.SK_GESTAO
    GROUP BY GESTAO.ID_COD, GESTAO.NOME_GESTAO
    ORDER BY SUM([F_Despesa].VALOR_EMPENHADO) DESC
GO

Commands completed successfully.

(10 rows affected)

Total execution time: 00:00:00.350

COD_GESTAO NOME_GESTAO VALOR_EMPENHADO 1 TESOURO NACIONAL R$ 1.390.308.288.733,03 57904 FUNDO DO REGIME GERAL DA PREVIDENCIA SOCIAL R$ 326.083.482.989,95 57202 INSTITUTO NACIONAL DO SEGURO SOCIAL R$ 77.916.179.496,24 15253 FUNDO NACIONAL DE DESENVOLVIMENTO DA EDUCACAO R$ 56.432.411.665,29 32396 AGENCIA NACIONAL DE MINERACAO R$ 7.839.608.876,44 32205 AGENCIA NACIONAL DO PETROLEO R$ 7.400.252.786,59 26443 EMPRESA BRASILEIRA DE SERVICOS HOSPITALARES R$ 5.964.701.253,31 32210 AGENCIA NACIONAL DE ENERGIA ELETRICA R$ 4.289.109.262,96 25201 FUNDACAO OSWALDO CRUZ R$ 3.249.557.022,91 13203 EMPRESA BRASILEIRA DE PESQUISA AGROPECUARIA R$ 3.126.911.895,80

5- Qual o total mês a mês de Valor Liquidado (R$) para cada Grupo de Despesa?

In [35]:
USE DW_09
GO

SELECT 
    FORMAT([F_Despesa].DATA_MES, 'MM/yyyy') AS MES, 
    DESPESA.ID_COD AS COD_GRP_DESPESA, 
    DESPESA.NOME_GRP_DESPESA, 
    FORMAT(SUM([F_Despesa].VALOR_LIQUIDADO), 'C', 'pt-br') AS VALOR_LIQUIDADO 

FROM [DW_09].[GOLD].[F_Despesa]
    INNER JOIN [DW_09].[SILVER].[D_Grp_Despesa] DESPESA ON [DW_09].[GOLD].[F_Despesa].SK_GRP_DESPESA = DESPESA.SK_GRP_DESPESA
    GROUP BY [F_Despesa].DATA_MES, DESPESA.ID_COD, DESPESA.NOME_GRP_DESPESA
    ORDER BY DESPESA.ID_COD ASC, MONTH([F_Despesa].DATA_MES) ASC
GO

Commands completed successfully.

(18 rows affected)

Total execution time: 00:00:00.354

MES COD_GRP_DESPESA NOME_GRP_DESPESA VALOR_LIQUIDADO 01/2022 1 Pessoal e Encargos Sociais R$ 21.985.023.367,84 02/2022 1 Pessoal e Encargos Sociais R$ 22.398.684.910,42 03/2022 1 Pessoal e Encargos Sociais R$ 22.420.460.342,13 01/2022 2 Juros e Encargos da Dívida R$ 52.288.306.158,19 02/2022 2 Juros e Encargos da Dívida R$ 38.460.931.941,51 03/2022 2 Juros e Encargos da Dívida R$ 2.065.735.373,50 01/2022 3 Outras Despesas Correntes R$ 99.502.251.625,93 02/2022 3 Outras Despesas Correntes R$ 143.524.940.293,42 03/2022 3 Outras Despesas Correntes R$ 136.782.639.197,69 01/2022 4 Investimentos R$ 9.046.342,28 02/2022 4 Investimentos R$ 223.369.485,02 03/2022 4 Investimentos R$ 1.970.134.671,61 01/2022 5 Inversões Financeiras R$ 4.276.460.267,33 02/2022 5 Inversões Financeiras R$ 3.085.099.995,05 03/2022 5 Inversões Financeiras R$ 5.462.834.225,47 01/2022 6 Amortização/Refinanciamento da Dívida R$ 165.905.512.842,46 02/2022 6 Amortização/Refinanciamento da Dívida R$ 3.396.754.006,30 03/2022 6 Amortização/Refinanciamento da Dívida R$ 288.397.081.749,19

6- Quais os TOP 10 Grupo de Despesas referente a valor Liquidado (R$) em Fev/2022?

In [36]:
USE DW_09
GO

SELECT TOP 10 
    FORMAT([F_Despesa].DATA_MES, 'MM/yyyy') AS MES, 
    DESPESA.ID_COD AS COD_GRP_DESPESA, 
    DESPESA.NOME_GRP_DESPESA, 
    FORMAT(SUM([F_Despesa].VALOR_LIQUIDADO), 'C', 'pt-br') AS VALOR_LIQUIDADO 

FROM [DW_09].[GOLD].[F_Despesa]
    INNER JOIN [DW_09].[SILVER].[D_Grp_Despesa] DESPESA ON [DW_09].[GOLD].[F_Despesa].SK_GRP_DESPESA = DESPESA.SK_GRP_DESPESA
    WHERE MONTH([F_Despesa].DATA_MES) = 2
    GROUP BY [F_Despesa].DATA_MES, DESPESA.ID_COD, DESPESA.NOME_GRP_DESPESA    
    ORDER BY SUM([F_Despesa].VALOR_LIQUIDADO) DESC
GO

Commands completed successfully.

(6 rows affected)

Total execution time: 00:00:00.365

MES COD_GRP_DESPESA NOME_GRP_DESPESA VALOR_LIQUIDADO 02/2022 3 Outras Despesas Correntes R$ 143.524.940.293,42 02/2022 2 Juros e Encargos da Dívida R$ 38.460.931.941,51 02/2022 1 Pessoal e Encargos Sociais R$ 22.398.684.910,42 02/2022 6 Amortização/Refinanciamento da Dívida R$ 3.396.754.006,30 02/2022 5 Inversões Financeiras R$ 3.085.099.995,05 02/2022 4 Investimentos R$ 223.369.485,02

7- Qual a variação %(MoM) de Valor Empenhado (R$) de Mar/2022 para Fev/2022 por Unidade Gestora

In [37]:
USE DW_09
GO

-- CRIAÇÃO DA TABELA COM A SOMA DO VALOR EMPENHADO POR UNIDADE GESTORA NO MÊS DE FEVEREIRO
WITH ORG_SUP_EMPENHADO AS (
    SELECT GESTORA.ID_COD AS COD_UNID_GESTORA, GESTORA.SK_UNID_GESTORA, GESTORA.NOME_UNID_GESTORA, SUM([F_Despesa].VALOR_EMPENHADO) AS VALOR_EMPENHADO , 
    SUM([F_Despesa].VALOR_EMPENHADO) AS VALOR_DIV
    FROM [DW_09].[GOLD].[F_Despesa]
    INNER JOIN [DW_09].[SILVER].[D_Unid_Gestora] GESTORA ON [DW_09].[GOLD].[F_Despesa].SK_UNID_GESTORA = GESTORA.SK_UNID_GESTORA
    WHERE MONTH([F_Despesa].DATA_MES) = 2

    GROUP BY [F_Despesa].DATA_MES, GESTORA.SK_UNID_GESTORA, GESTORA.ID_COD, GESTORA.NOME_UNID_GESTORA    
)

SELECT 
    GESTORA.ID_COD AS COD_UNID_GESTORA, 
    GESTORA.NOME_UNID_GESTORA,    
    FORMAT(ORG_SUP_EMPENHADO.VALOR_EMPENHADO, 'C', 'pt-br') AS VALOR_EMPENHADO_FEV,
    FORMAT(SUM([F_Despesa].VALOR_EMPENHADO), 'C', 'pt-br') AS VALOR_EMPENHADO_MAR,
    CASE WHEN ORG_SUP_EMPENHADO.VALOR_DIV = 0 THEN NULL ELSE
    FORMAT(((SUM([F_Despesa].VALOR_EMPENHADO)-ORG_SUP_EMPENHADO.VALOR_EMPENHADO)/ORG_SUP_EMPENHADO.VALOR_DIV), 'P') END AS PORCENTAGEM_MOM,
    FORMAT((SUM([F_Despesa].VALOR_EMPENHADO)-ORG_SUP_EMPENHADO.VALOR_EMPENHADO), 'C', 'pt-br') AS VARIACAO_VALOR_EMPENHADO 

FROM [DW_09].[GOLD].[F_Despesa]
    INNER JOIN [DW_09].[SILVER].[D_Unid_Gestora] GESTORA ON [DW_09].[GOLD].[F_Despesa].SK_UNID_GESTORA = GESTORA.SK_UNID_GESTORA
    INNER JOIN ORG_SUP_EMPENHADO ON [DW_09].[GOLD].[F_Despesa].SK_UNID_GESTORA = ORG_SUP_EMPENHADO.SK_UNID_GESTORA
    WHERE MONTH([F_Despesa].DATA_MES) = 3
    
    GROUP BY GESTORA.ID_COD, GESTORA.NOME_UNID_GESTORA, ORG_SUP_EMPENHADO.VALOR_EMPENHADO, ORG_SUP_EMPENHADO.VALOR_DIV
    ORDER BY VARIACAO_VALOR_EMPENHADO DESC
GO


Commands completed successfully.

(3127 rows affected)

Total execution time: 00:00:00.776

COD_UNID_GESTORA NOME_UNID_GESTORA VALOR_EMPENHADO_FEV VALOR_EMPENHADO_MAR PORCENTAGEM_MOM VARIACAO_VALOR_EMPENHADO 135179 UA/PICOS R$ 96,02 R$ 1.088,86 1,033.99% R$ 992,84 154359 FUNDACAO UNIVERSIDADE FEDERAL DO PAMPA R$ 2.440.904,15 R$ 3.431.879,25 40.60% R$ 990.975,10 364150 CNPQ - ATIVIDADES NO EXTERIOR R$ 514.123,67 R$ 613.816,84 19.39% R$ 99.693,17 167110 COLEGIO MILITAR DE JUIZ DE FORA R$ 19.821,17 R$ 119.428,25 502.53% R$ 99.607,08 158431 INST.FED.DE GOIAS/CAMPUS JATAI R$ 242.895,86 R$ 143.335,80 -40.99% -R$ 99.560,06 158472 IFPB - CAMPUS MONTEIRO R$ 11.159,15 R$ 110.380,08 889.14% R$ 99.220,93 193003 DNOCS CEST/CE - FORTALEZA-CE R$ 1.736.432,00 R$ 746.927,50 -56.98% -R$ 989.504,50 257021 DISTRITO SANIT.ESP.INDIGENA - ALTO RIO JURUA R$ 989.318,20 R$ 0,00 -100.00% -R$ 989.318,20 158134 INST.FED.DE EDUC.,CIENC.E TEC.DE SERGIPE R$ 20.620.777,08 R$ 21.607.815,81 4.79% R$ 987.038,73 155016 EBSERH HU-UFGD R$ 2.794.627,19 R$ 3.775.599,85 35.10% R$ 980.972,66 158971 INST.FED.MATO GROSSO/CAMPUS VARZEA GRANDE R$ 170.094,72 R$ 71.340,75 -58.06% -R$ 98.753,97 514286 FRGPS - GERENCIA EXECUTIVA IMPERATRIZ R$ 242.696,66 R$ 143.954,00 -40.69% -R$ 98.742,66 240054 CONSULADO-GERAL DO BRASIL EM SAO FRANCISCO R$ 952.129,95 R$ 853.508,93 -10.36% -R$ 98.621,02 153119 PREFEITURA DA UNIVERSIDADE DA UFRJ R$ 109.265,70 R$ 10.660,60 -90.24% -R$ 98.605,10 155217 IFPE - CAMPUS PAULISTA R$ 29.015,85 R$ 127.593,00 339.74% R$ 98.577,15 514270 FRGPS - GERENCIA EXECUTIVA SAO LUIS R$ 99.459,77 R$ 1.061,80 -98.93% -R$ 98.397,97 257026 DISTRITO SANIT.ESP.INDIGENA - JAVARI R$ 1.020,36 R$ 99.384,39 9,640.13% R$ 98.364,03 167287 BIBLIOTECA DO EXERCITO R$ 0,00 R$ 98.358,76 NULL R$ 98.358,76 240056 EMBAIXADA DO BRASIL EM MADRI R$ 895.697,08 R$ 797.572,22 -10.96% -R$ 98.124,86 183038 INSTITUTO NACIONAL DA PROPRIEDADE INDUSTRIAL R$ 5.658.637,94 R$ 6.634.396,29 17.24% R$ 975.758,35 160303 BASE DE ADMINISTRACAO E APOIO DA 1 RM R$ 2.465.135,69 R$ 1.489.971,75 -39.56% -R$ 975.163,94 167545 HOSPITAL DE GUARN. DE S. GABRIEL DA CACHOEIRA R$ 1.056.105,81 R$ 82.655,41 -92.17% -R$ 973.450,40 200324 DEPEN/DIRETORIA DE POLITICAS PENITENCIARIAS R$ 0,00 R$ 972.455,50 NULL R$ 972.455,50 158610 INST.FED.DE GOIAS/CAMPUS APARECIDA DE GOIANIA R$ 105.016,21 R$ 202.882,66 93.19% R$ 97.866,45 156059 INSTITUTO FEDERAL DA BAHIA-BRUMADO R$ 126.681,97 R$ 224.497,18 77.21% R$ 97.815,21 323121 GERENCIA REGIONAL DA ANM - RO -R$ 53.672,61 R$ 43.966,17 -181.92% R$ 97.638,78 152757 INSTITUTO FEDERAL DO RN - CAMPUS NOVA CRUZ R$ 21.000,00 R$ 118.568,94 464.61% R$ 97.568,94 114625 UNIDADE ESTADUAL DO IBGE NO RIO GRANDE DO SUL R$ 501.937,16 R$ 599.470,79 19.43% R$ 97.533,63 254445 INSTITUTO DE TECNOLOGIA EM IMUNOBIOLOGICOS R$ 333.399.154,00 R$ 235.873.305,23 -29.25% -R$ 97.525.848,77 160407 29 BATALHAO DE INFANTARIA BLINDADO R$ 250.983,98 R$ 153.469,17 -38.85% -R$ 97.514,81 160159 18 GRUPO DE ARTILHARIA DE CAMPANHA R$ 11.984,94 R$ 109.279,18 811.80% R$ 97.294,24 158382 INST.FED. ALAGOAS/CAMPUS SATUBA R$ 262.574,31 R$ 359.781,29 37.02% R$ 97.206,98 158298 IF GOIANO - CAMPUS URUTAI R$ 31.642,06 R$ 1.000.659,41 3,062.43% R$ 969.017,35 440001 SUBSECRET.DE PLANEJ.,ORC.E ADMINIST.±SPOA/MMA R$ 4.405.328,83 R$ 3.436.946,41 -21.98% -R$ 968.382,42 343015 MUSEU IMPERIAL - PETROPOLIS R$ 884.613,11 -R$ 75.566,00 -108.54% -R$ 960.179,11 443043 INST.CHICO MENDES DE CONSER.DA BIODIVERSIDADE -R$ 572.337,23 -R$ 1.532.388,53 167.74% -R$ 960.051,30 710100 TRIBUNAL MARITIMO R$ 63.522,10 R$ 160.521,29 152.70% R$ 96.999,19 253002 AGENCIA NACIONAL DE VIGILANCIA SANITARIA R$ 3.885.485,31 R$ 100.857.924,70 2,495.76% R$ 96.972.439,39 167049 10º DEPOSITO DE SUPRIMENTO R$ 16.915,64 R$ 112.980,79 567.91% R$ 96.065,15 155911 HOSPITAL UNIVERSITARIO GAFFREE E GUINLE R$ 1.977.020,53 R$ 2.935.947,01 48.50% R$ 958.926,48 170088 SUPERINTENDENCIA REGIONAL DA RFB NA 6A RF R$ 1.098.846,23 R$ 2.056.897,51 87.19% R$ 958.051,28 240016 INSTITUTO RIO-BRANCO R$ 120.000,00 R$ 120.957,28 0.80% R$ 957,28 150182 PRO-REITORIA DE ADMINISTRACAO/UFF 

8- Retorno o maior Valor Empenhado (R$) de Grupo de despesas em Fev/2022 para cada Órgão Superior

In [38]:
USE DW_09
GO

-- TABELA COM PARTIÇÃO POR ÓRGÃO SUPERIOR 
WITH ORG_SUP_EMPENHADO AS (
    SELECT DISTINCT RANK() OVER (PARTITION BY SK_ORG_SUPERIOR ORDER BY SUM(VALOR_EMPENHADO) DESC) AS RANK_SUP_EMPENHADO, 
    DATA_MES, SK_ORG_SUPERIOR, SK_GRP_DESPESA, SUM(VALOR_EMPENHADO) AS VALOR_SUM_EMPENHADO 

    FROM [DW_09].[GOLD].[F_Despesa]
            WHERE MONTH([F_Despesa].DATA_MES) = 2
            GROUP BY DATA_MES, SK_ORG_SUPERIOR, SK_GRP_DESPESA
)

SELECT 
    FORMAT([ORG_SUP_EMPENHADO].DATA_MES, 'MM/yyyy') AS MES, 
    SUPERIOR.ID_COD AS COD_ORD_SUPERIOR, 
    SUPERIOR.NOME_ORG_SUPERIOR, 
    DESPESA.ID_COD AS COD_GRP_DESPESA, 
    DESPESA.NOME_GRP_DESPESA, 
    FORMAT(MAX([ORG_SUP_EMPENHADO].VALOR_SUM_EMPENHADO), 'C', 'pt-br') AS MAIOR_VALOR_EMPENHADO 
FROM [ORG_SUP_EMPENHADO]
    INNER JOIN [DW_09].[SILVER].[D_Org_Superior] SUPERIOR ON [ORG_SUP_EMPENHADO].SK_ORG_SUPERIOR = SUPERIOR.SK_ORG_SUPERIOR
    INNER JOIN [DW_09].[SILVER].[D_Grp_Despesa] DESPESA ON [ORG_SUP_EMPENHADO].SK_GRP_DESPESA = DESPESA.SK_GRP_DESPESA
    WHERE MONTH([ORG_SUP_EMPENHADO].DATA_MES) = 2 AND RANK_SUP_EMPENHADO = 1
    GROUP BY [ORG_SUP_EMPENHADO].DATA_MES, SUPERIOR.ID_COD, SUPERIOR.NOME_ORG_SUPERIOR, DESPESA.ID_COD, DESPESA.NOME_GRP_DESPESA
    ORDER BY SUM([ORG_SUP_EMPENHADO].VALOR_SUM_EMPENHADO) ASC

Commands completed successfully.

(21 rows affected)

Total execution time: 00:00:00.372

MES COD_ORD_SUPERIOR NOME_ORG_SUPERIOR COD_GRP_DESPESA NOME_GRP_DESPESA MAIOR_VALOR_EMPENHADO 02/2022 37000 Controladoria-Geral da União 3 Outras Despesas Correntes R$ 3.468.158,65 02/2022 81000 Ministério da Mulher, Família e Direitos Huma 3 Outras Despesas Correntes R$ 20.337.603,89 02/2022 63000 Advocacia-Geral da União 3 Outras Despesas Correntes R$ 22.161.996,66 02/2022 30000 Ministério da Justiça e Segurança Pública 3 Outras Despesas Correntes R$ 36.573.561,45 02/2022 44000 Ministério do Meio Ambiente 3 Outras Despesas Correntes R$ 52.665.571,72 02/2022 54000 Ministério do Turismo 3 Outras Despesas Correntes R$ 59.691.721,38 02/2022 41000 Ministério das Comunicações 3 Outras Despesas Correntes R$ 89.627.632,77 02/2022 35000 Ministério das Relações Exteriores 3 Outras Despesas Correntes R$ 176.775.773,90 02/2022 24000 Ministério da Ciência, Tecnologia, Inovações 3 Outras Despesas Correntes R$ 186.517.312,94 02/2022 25201 Banco Central do Brasil - Orçamento Fiscal e 1 Pessoal e Encargos Sociais R$ 279.500.000,00 02/2022 22000 Ministério da Agricultura, Pecuária e Abastec 1 Pessoal e Encargos Sociais R$ 294.351.808,70 02/2022 20000 Presidência da República 1 Pessoal e Encargos Sociais R$ 301.010.473,50 02/2022 39000 Ministério da Infraestrutura 4 Investimentos R$ 333.695.946,12 02/2022 52000 Ministério da Defesa 1 Pessoal e Encargos Sociais R$ 1.664.749.006,78 02/2022 53000 Ministério do Desenvolvimento Regional 5 Inversões Financeiras R$ 3.782.332.699,00 02/2022 26000 Ministério da Educação 3 Outras Despesas Correntes R$ 7.326.425.913,42 02/2022 36000 Ministério da Saúde 3 Outras Despesas Correntes R$ 10.299.132.971,54 02/2022 32000 Ministério de Minas e Energia 3 Outras Despesas Correntes R$ 10.863.792.096,42 02/2022 40000 Ministério do Trabalho 3 Outras Despesas Correntes R$ 15.136.914.122,21 02/2022 55000 Ministério da Cidadania 3 Outras Despesas Correntes R$ 54.636.673.082,81 02/2022 25000 Ministério da Economia 6 Amortização/Refinanciamento da Dívida R$ 295.708.836.228,28

9- Retorne o % de Valor Pago (R$) sobre o total, por Gestão Fev/2022

In [39]:
USE DW_09
GO

SELECT 
    FORMAT([F_Despesa].DATA_MES, 'MM/yyyy') AS MES, 
    GESTAO.ID_COD AS COD_GESTAO, 
    GESTAO.NOME_GESTAO, 
    FORMAT(SUM([F_Despesa].VALOR_PAGO)/(SELECT SUM([F_Despesa].VALOR_PAGO) FROM [DW_09].[GOLD].[F_Despesa]), 'P') AS PORCENTAGEM,
    FORMAT(SUM([F_Despesa].VALOR_PAGO), 'C', 'pt-br') AS VALOR_PAGO 

FROM [DW_09].[GOLD].[F_Despesa]
    INNER JOIN [DW_09].[SILVER].[D_Gestao] GESTAO ON [DW_09].[GOLD].[F_Despesa].SK_GESTAO = GESTAO.SK_GESTAO
    WHERE MONTH([F_Despesa].DATA_MES) = 2
    GROUP BY [F_Despesa].DATA_MES, GESTAO.ID_COD, GESTAO.NOME_GESTAO
    ORDER BY SUM([F_Despesa].VALOR_PAGO) DESC
GO

Commands completed successfully.

(187 rows affected)

Total execution time: 00:00:00.377

MES COD_GESTAO NOME_GESTAO PORCENTAGEM VALOR_PAGO 02/2022 1 TESOURO NACIONAL 13.51% R$ 127.565.331.310,81 02/2022 57904 FUNDO DO REGIME GERAL DA PREVIDENCIA SOCIAL 6.19% R$ 58.393.000.644,05 02/2022 57202 INSTITUTO NACIONAL DO SEGURO SOCIAL 0.74% R$ 7.013.442.210,25 02/2022 15253 FUNDO NACIONAL DE DESENVOLVIMENTO DA EDUCACAO 0.41% R$ 3.868.747.981,87 02/2022 32205 AGENCIA NACIONAL DO PETROLEO 0.39% R$ 3.692.127.204,12 02/2022 26443 EMPRESA BRASILEIRA DE SERVICOS HOSPITALARES 0.05% R$ 486.936.956,88 02/2022 17804 BANCO CENTRAL DO BRASIL 0.03% R$ 292.394.460,20 02/2022 15236 UNIVERSIDADE FEDERAL DO RIO DE JANEIRO 0.03% R$ 289.394.176,59 02/2022 25201 FUNDACAO OSWALDO CRUZ 0.02% R$ 227.875.266,67 02/2022 32210 AGENCIA NACIONAL DE ENERGIA ELETRICA 0.02% R$ 226.518.891,22 02/2022 13203 EMPRESA BRASILEIRA DE PESQUISA AGROPECUARIA 0.02% R$ 226.444.052,60 02/2022 11301 FUNDACAO INSTITUTO BRAS.GEOGR. E ESTATISTICA 0.02% R$ 186.637.576,31 02/2022 15229 UNIVERSIDADE FEDERAL DE MINAS GERAIS 0.02% R$ 183.142.102,45 02/2022 15227 UNIVERSIDADE FEDERAL FLUMINENSE 0.02% R$ 174.586.673,80 02/2022 15279 FUND.COORD.DE APERF.DE PESSOAL NIVEL SUPERIOR 0.02% R$ 172.860.295,55 02/2022 15223 UNIVERSIDADE FEDERAL DA BAHIA 0.02% R$ 146.592.929,64 02/2022 15231 UNIVERSIDADE FEDERAL DA PARAIBA 0.02% R$ 144.104.778,77 02/2022 15235 UNIVERSIDADE FEDERAL DO RIO GRANDE DO SUL 0.02% R$ 142.963.856,67 02/2022 36211 FUNDACAO NACIONAL DE SAUDE 0.01% R$ 137.623.927,94 02/2022 15237 UNIVERSIDADE FEDERAL DE SANTA CATARINA 0.01% R$ 136.957.567,39 02/2022 15232 UNIVERSIDADE FEDERAL DO PARANA 0.01% R$ 136.040.991,19 02/2022 15257 FUNDACAO UNIVERSIDADE DE BRASILIA 0.01% R$ 133.939.374,47 02/2022 15233 UNIVERSIDADE FEDERAL DE PERNAMBUCO 0.01% R$ 132.139.446,58 02/2022 15234 UNIVERSIDADE FEDERAL DO RIO GRANDE DO NORTE 0.01% R$ 131.437.051,21 02/2022 36210 HOSPITAL NOSSA SENHORA DA CONCEICAO S/A 0.01% R$ 126.080.395,81 02/2022 15224 UNIVERSIDADE FEDERAL DO CEARA 0.01% R$ 124.250.988,23 02/2022 15275 HOSPITAL DE CLINICAS DE PORTO ALEGRE 0.01% R$ 123.368.808,92 02/2022 15260 FUNDACAO UNIVERSIDADE FEDERAL DE UBERLANDIA 0.01% R$ 116.116.020,83 02/2022 15238 UNIVERSIDADE FEDERAL DE SANTA MARIA - RS 0.01% R$ 113.726.669,52 02/2022 15230 UNIVERSIDADE FEDERAL DO PARA 0.01% R$ 112.962.641,51 02/2022 15250 UNIVERSIDADE FEDERAL DE SAO PAULO 0.01% R$ 108.785.422,62 02/2022 27209 COMPANHIA BRASILEIRA DE TRENS URBANOS 0.01% R$ 103.601.252,82 02/2022 15226 UNIVERSIDADE FEDERAL DE GOIAS 0.01% R$ 97.885.495,91 02/2022 37201 INSTITUTO NAC. DE COLONIZACAO E REF.AGRARIA 0.01% R$ 92.389.182,40 02/2022 19211 INST.BRAS.DO MEIO-AMBIENTE E DOS REC.NAT.REN. 0.01% R$ 91.371.879,60 02/2022 39252 DEPTO. NAC. DE INFRA±ESTRUTURA DE TRANSPORTES 0.01% R$ 90.990.019,29 02/2022 22211 COMPANHIA NACIONAL DE ABASTECIMENTO 0.01% R$ 89.628.033,26 02/2022 15225 UNIVERSIDADE FEDERAL DO ESPIRITO SANTO 0.01% R$ 78.994.910,36 02/2022 15246 UNIVERSIDADE TECNOLOGICA FEDERAL DO PARANA 0.01% R$ 71.673.977,83 02/2022 26439 INST.FED.DE EDUC.,CIENC.E TEC.DE SAO PAULO 0.01% R$ 70.904.271,53 02/2022 15258 FUNDACAO UNIVERSIDADE DO MARANHAO 0.01% R$ 70.602.003,13 02/2022 36201 CONSELHO NAC.DE DESENV.CIENTIFICO TECNOLOGICO 0.01% R$ 69.778.490,83 02/2022 15222 UNIVERSIDADE FEDERAL DE ALAGOAS 0.01% R$ 69.451.004,41 02/2022 15228 UNIVERSIDADE FEDERAL DE JUIZ DE FORA 0.01% R$ 68.652.335,99 02/2022 15268 UNIVERSIDADE FEDERAL DE VICOSA 0.01% R$ 68.279.661,65 02/2022 15269 FUNDACAO UNIVERSIDADE FEDERAL DE MATO G. SUL 0.01% R$ 67.890.510,51 02/2022 15262 FUNDACAO UNIVERSIDADE FEDERAL DE MATO GROSSO 0.01% R$ 63.989.759,55 02/2022 15264 FUNDACAO UNIVERSIDADE FEDERAL DE PELOTAS 0.01% R$ 63.848.802,33 02/2022 11501 COMISSAO NACIONAL DE ENERGIA NUCLEAR 0.01% R$ 62.341.383,49 02/2022 11201 CIA DE DESENV DOS VALES DO S.FRANC.E PARNAIBA 0.01% R$ 59.412.075,95 02/2022 15267 FUNDACAO UNIVERSIDADE FEDERAL DE SERGIPE 0.01% R$ 58.425.356,51 02/2022 15256 FUNDACAO UNIVERSIDADE DO AMAZONAS 0.01% R$ 58.192.312,83 02/2022 15281 UNIVERSIDADE FEDERAL DE C

10- Retorne o valor média de Valor Pago (R$) por despesa agrupado por Gestão

In [40]:
USE DW_09
GO

-- TABELA COM PARTIÇÃO POR GESTAO
WITH GEST_PAGO AS (
    SELECT DISTINCT RANK() OVER (PARTITION BY SK_GESTAO ORDER BY SUM(VALOR_PAGO) DESC) AS RANK_GEST_PAGO, 
    DATA_MES, SK_GESTAO, SK_GRP_DESPESA, SUM(VALOR_PAGO) AS VALOR_SUM_PAGO 
    FROM [DW_09].[GOLD].[F_Despesa]
            GROUP BY DATA_MES, SK_GESTAO, SK_GRP_DESPESA
)

SELECT 
    GESTAO.ID_COD AS COD_GESTAO, 
    GESTAO.NOME_GESTAO, 
    DESPESA.ID_COD AS COD_GRP_DESPESA, 
    DESPESA.NOME_GRP_DESPESA, 
    FORMAT(AVG([GEST_PAGO].VALOR_SUM_PAGO), 'C', 'pt-br') AS MEDIA_VALOR_PAGO 
FROM [GEST_PAGO]
    INNER JOIN [DW_09].[SILVER].[D_Gestao] GESTAO ON [GEST_PAGO].SK_GESTAO = GESTAO.SK_GESTAO
    INNER JOIN [DW_09].[SILVER].[D_Grp_Despesa] DESPESA ON [GEST_PAGO].SK_GRP_DESPESA = DESPESA.SK_GRP_DESPESA
    GROUP BY GESTAO.ID_COD, GESTAO.NOME_GESTAO, DESPESA.ID_COD, DESPESA.NOME_GRP_DESPESA
    ORDER BY GESTAO.NOME_GESTAO ASC, SUM([GEST_PAGO].VALOR_SUM_PAGO) ASC

Commands completed successfully.

(568 rows affected)

Total execution time: 00:00:00.376

COD_GESTAO NOME_GESTAO COD_GRP_DESPESA NOME_GRP_DESPESA MEDIA_VALOR_PAGO 20402 AGENCIA ESPACIAL BRASILEIRA - AEB 4 Investimentos R$ 0,00 20402 AGENCIA ESPACIAL BRASILEIRA - AEB 3 Outras Despesas Correntes R$ 402.536,48 20402 AGENCIA ESPACIAL BRASILEIRA - AEB 1 Pessoal e Encargos Sociais R$ 817.769,43 44205 AGENCIA NACIONAL DE AGUAS - ANA 4 Investimentos R$ 8.075,49 44205 AGENCIA NACIONAL DE AGUAS - ANA 3 Outras Despesas Correntes R$ 2.989.205,60 44205 AGENCIA NACIONAL DE AGUAS - ANA 1 Pessoal e Encargos Sociais R$ 6.535.179,58 20214 AGENCIA NACIONAL DE AVIACAO CIVIL 4 Investimentos R$ 0,00 20214 AGENCIA NACIONAL DE AVIACAO CIVIL 3 Outras Despesas Correntes R$ 5.076.556,01 20214 AGENCIA NACIONAL DE AVIACAO CIVIL 1 Pessoal e Encargos Sociais R$ 23.426.079,49 32210 AGENCIA NACIONAL DE ENERGIA ELETRICA 4 Investimentos R$ 92,15 32210 AGENCIA NACIONAL DE ENERGIA ELETRICA 1 Pessoal e Encargos Sociais R$ 11.693.558,19 32210 AGENCIA NACIONAL DE ENERGIA ELETRICA 3 Outras Despesas Correntes R$ 222.170.637,17 32396 AGENCIA NACIONAL DE MINERACAO 4 Investimentos R$ 31.576,42 32396 AGENCIA NACIONAL DE MINERACAO 1 Pessoal e Encargos Sociais R$ 15.343.029,75 32396 AGENCIA NACIONAL DE MINERACAO 3 Outras Despesas Correntes R$ 276.251.738,44 36213 AGENCIA NACIONAL DE SAUDE SUPLEMENTAR 4 Investimentos R$ 0,00 36213 AGENCIA NACIONAL DE SAUDE SUPLEMENTAR 5 Inversões Financeiras R$ 133.609,46 36213 AGENCIA NACIONAL DE SAUDE SUPLEMENTAR 3 Outras Despesas Correntes R$ 3.935.225,37 36213 AGENCIA NACIONAL DE SAUDE SUPLEMENTAR 1 Pessoal e Encargos Sociais R$ 11.960.301,94 41231 AGENCIA NACIONAL DE TELECOMUNICACOES 4 Investimentos R$ 55.405,28 41231 AGENCIA NACIONAL DE TELECOMUNICACOES 3 Outras Despesas Correntes R$ 3.770.083,16 41231 AGENCIA NACIONAL DE TELECOMUNICACOES 1 Pessoal e Encargos Sociais R$ 24.141.706,86 68201 AGENCIA NACIONAL DE TRANSPORTES AQUAVIARIOS 4 Investimentos R$ 6.155,00 68201 AGENCIA NACIONAL DE TRANSPORTES AQUAVIARIOS 3 Outras Despesas Correntes R$ 983.598,35 68201 AGENCIA NACIONAL DE TRANSPORTES AQUAVIARIOS 1 Pessoal e Encargos Sociais R$ 6.724.626,53 39250 AGENCIA NACIONAL DE TRANSPORTES TERRESTRES 4 Investimentos R$ 0,00 39250 AGENCIA NACIONAL DE TRANSPORTES TERRESTRES 3 Outras Despesas Correntes R$ 5.919.890,50 39250 AGENCIA NACIONAL DE TRANSPORTES TERRESTRES 1 Pessoal e Encargos Sociais R$ 16.097.969,53 36212 AGENCIA NACIONAL DE VIGILANCIA SANITARIA 4 Investimentos R$ 37.397,86 36212 AGENCIA NACIONAL DE VIGILANCIA SANITARIA 3 Outras Despesas Correntes R$ 4.307.814,53 36212 AGENCIA NACIONAL DE VIGILANCIA SANITARIA 1 Pessoal e Encargos Sociais R$ 36.801.658,24 32205 AGENCIA NACIONAL DO PETROLEO 4 Investimentos R$ 2.666,67 32205 AGENCIA NACIONAL DO PETROLEO 1 Pessoal e Encargos Sociais R$ 14.764.170,04 32205 AGENCIA NACIONAL DO PETROLEO 3 Outras Despesas Correntes R$ 2.379.502.074,75 52233 AMAZONIA AZUL TECNOLOGIAS DE DEFESA S.A. 4 Investimentos R$ 18.109,88 52233 AMAZONIA AZUL TECNOLOGIAS DE DEFESA S.A. 3 Outras Despesas Correntes R$ 885.249,68 52233 AMAZONIA AZUL TECNOLOGIAS DE DEFESA S.A. 1 Pessoal e Encargos Sociais R$ 15.248.557,81 20203 ANCINE-AGENCIA NACIONAL DO CINEMA 4 Investimentos R$ 0,00 20203 ANCINE-AGENCIA NACIONAL DO CINEMA 3 Outras Despesas Correntes R$ 858.796,80 20203 ANCINE-AGENCIA NACIONAL DO CINEMA 1 Pessoal e Encargos Sociais R$ 5.885.827,63 17804 BANCO CENTRAL DO BRASIL 4 Investimentos R$ 1.854.148,44 17804 BANCO CENTRAL DO BRASIL 3 Outras Despesas Correntes R$ 24.719.532,28 17804 BANCO CENTRAL DO BRASIL 1 Pessoal e Encargos Sociais R$ 175.505.062,96 34209 BIBLIOTECA NACIONAL 4 Investimentos R$ 0,00 34209 BIBLIOTECA NACIONAL 3 Outras Despesas Correntes R$ 1.135.719,82 34209 BIBLIOTECA NACIONAL 1 Pessoal e Encargos Sociais R$ 3.857.971,40 21201 CAIXA DE CONSTRUCAO DE CASAS P/PESSOAL DO MM 4 Investimentos R$ 0,00 21201 CAIXA DE CONSTRUCAO DE CASAS P/PESSOAL DO MM 2 Juros e Encargos da Dívida R$ 7.152,70 21201 CAIXA DE CONSTRUCAO DE CASAS P/PESSOAL DO MM 3 Outras Despesas Correntes R$ 21.630,84 21201 CAIXA DE C